# Summary stats of data - part 13
--------------------

## OVERVIEW



## OBJECTIVE: ✅ Summarize the quantification data per cell
In this notebook, the logic for creating per cell summary statsistics from the quantification output is outlined.


### Metrics we care about:

1. Organelles & Contact Sites:
    
    Size:
    - number of objects per cell (not perfect) [X]
    - volume fraction per cell [X]
    - total/mean/median/standard deviation object volume per cell (not perfect) [X]
    - total/mean/median/standard deviation surface area per cell (not perfect) [X]
    
    Shape:
    - mean/median/std surface area to volume ratio per cell [X]
    - mean/median/std equivalent diameter per cell [X]
    - mean/median/std extent per cell [X]
    - mean/median/std euler number per cell [X]
    - mean/median/std solidity per cell [X]
    - mean/median/std major axis length per cell [X]
    
    Distribution:
    - mean/**median**/mode/min/max/**range**/**std**/**skew**/kurtosis/**variance** across area normalized XY bins (bold indicates the best summary measurements) [X]
    - ~~mean/median/mode/min/max/range/std/skew/kurtosis/variance across XY wedges~~
    - mean/**median**/mode/min/max/**range**/**std**/**skew**/kurtosis/**variance** across area normalized Z slices [X]

2. Contacts:
    
    Size:
    - total volume aXb contact site / total volume org A [X]
    - total volume aXb contact site / total volume org B [X]
    - percentage of individual org A objects (and org B, separately) involved in aXb contact [X]
    - mean/median/std contact site number per individual organelle per cell [X]
    - mean/median/std contact volume per individual organelle per cell [X]

3. Cell regions (no summary stats required for most):
    
    Size:
    - volume [X]
    - surface area [X]
    - nuc volume fraction [ ]
    
    Shape:
    - surface area to volume ratio [X]
    - equivalent diameter [X]
    - extent [X]
    - euler number [X]
    - solidity [X]
    - major axis length [X]
    
    Distribution:
    - mean/**median**/mode/min/max/**range**/**std**/**skew**/kurtosis/**variance** of nuc across area normalized XY bins [X]
    - ~~mean/median/mode/min/max/range/std/skew/kurtosis/variance of nuc across XY wedges~~
        
        NOTE: I think these values are going to throw off the statistics later because they are largely dependent on the orientation of the cell, but what I do think is important is the comparison of the mean/median/mode of each organelle in the cell (how similarly orientated are they?) and then comparing that cell-to-cell
        - comparison of mode, variance, and skew between organelles, but I think to compare betwen cells, they will have to be oriented to that, for example, bin 1 always has the highest org content, or maybe always has the highest golgi content since golgi is usually perinuclear and oriented by the centrosomes (I think?).
    - mean/**median**/mode/min/max/**range**/**std**/**skew**/kurtosis/**variance** of nuc across area normalized Z slices [X]

## `This to update`
1. remove stats measures for ER in almost all cases - ER_mean can be used for all shape, so median values can be removed; std has already been removed in most cases (one instance it wasn't though)
2. need to add volume fraction for contact sites
3. num_fraction of org in contact is messed up - only seeing 8 when I think there should be 15 columns



## IMPORTS

In [1]:
# top level imports
from pathlib import Path
import os, sys
from typing import Optional, Union, Dict, List
import itertools 
import glob

import time

import numpy as np
import pandas as pd

import napari

### import local python functions in ../infer_subc
sys.path.append(os.path.abspath((os.path.join(os.getcwd(), '..'))))

from infer_subc.core.file_io import (read_czi_image,
                                        export_inferred_organelle,
                                        import_inferred_organelle,
                                        export_tiff,
                                        list_image_files,
                                        read_tiff_image)



from infer_subc.constants import *
from infer_subc.utils.stats import *
from infer_subc.utils.stats_helpers import *
from infer_subc.utils.stats import _assert_uint16_labels
from infer_subc.core.img import label_uint16


import time
%load_ext autoreload
%autoreload 2

__________________
## 1. Read in the csv files

In [2]:
# root data path
data_root_path = Path(os.path.expanduser("~")) / "OneDrive/Desktop"

# quantification path
quant_data_path = data_root_path / "out"

# list files in the quant path
test_collect_csvs = sorted(quant_data_path.glob("*.csv"))
test_collect_csvs

[WindowsPath('C:/Users/redre/OneDrive/Desktop/out/skel_testa__contacts.csv'),
 WindowsPath('C:/Users/redre/OneDrive/Desktop/out/skel_testa__distributions.csv'),
 WindowsPath('C:/Users/redre/OneDrive/Desktop/out/skel_testa__organelles.csv'),
 WindowsPath('C:/Users/redre/OneDrive/Desktop/out/skel_testa__regions.csv')]

In [3]:
# collect each type of file in a different list
org_tabs = []
contact_tabs = []
dist_tabs = []
region_tabs = []
for stats_f in test_collect_csvs:
    stem = stats_f.stem
    
    org = "_organelles"
    contacts = "_contacts"
    dist = "_distributions"
    regions = "_regions"

    if org in stem:
        test_orgs = pd.read_csv(stats_f, index_col=0)
        test_orgs.insert(0, "dataset", "_".join(stats_f.stem.split("_")[:-1]))
        org_tabs.append(test_orgs)
    if contacts in stem:
        test_contact = pd.read_csv(stats_f, index_col=0)
        test_contact.insert(0, "dataset", "_".join(stats_f.stem.split("_")[:-1]))
        contact_tabs.append(test_contact)
    if dist in stem:
        test_dist = pd.read_csv(stats_f, index_col=0)
        test_dist.insert(0, "dataset", "_".join(stats_f.stem.split("_")[:-1]))
        dist_tabs.append(test_dist)
    if regions in stem:
        test_regions = pd.read_csv(stats_f, index_col=0)
        test_regions.insert(0, "dataset", "_".join(stats_f.stem.split("_")[:-1]))
        region_tabs.append(test_regions)

In [5]:
# when there are multiple of each type they will be concatenated together
org_df = pd.concat(org_tabs,axis=0, join='outer')
contacts_df = pd.concat(contact_tabs,axis=0, join='outer')
dist_df = pd.concat(dist_tabs,axis=0, join='outer')
regions_df = pd.concat(region_tabs,axis=0, join='outer')

### OPTIONAL: Adding in an option to collect from multiple file locations

In [7]:
test_multi_root_path = Path(os.path.expanduser("~")) / "Documents/Python_Scripts/Infer-subc/quant"

csv_path_list = [test_multi_root_path/"test_loc_1", test_multi_root_path/"test_loc_2" ]

csv_path_list

[WindowsPath('C:/Users/redre/Documents/Python_Scripts/Infer-subc/quant/test_loc_1'),
 WindowsPath('C:/Users/redre/Documents/Python_Scripts/Infer-subc/quant/test_loc_2')]

In [37]:
# list all files from each location in the list above
for loc in csv_path_list:
    files_store = sorted(loc.glob("*.csv"))
    for file in files_store:
        stem = file.stem.split("-")[0]
        print(stem)

20230921_TEST_contacts
20230921_TEST_distributions
20230921_TEST_organelles
20230922_newTEST_contacts
20230922_newTEST_distributions
20230922_newTEST_organelles


_______________________
## 2. Adding new columns to the individual tables before summarizing or combining

In [38]:
pd.set_option('display.max_columns', None)

#### Contacts: Counting the number of organelles involved in contact organelles in the org_df and normalizing the count and area to the organelle area

In [19]:
contacts_df.head(60)

dataset                                         image_name    object  \
0   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...     LD_ER   
1   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...     LD_ER   
2   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...     LD_ER   
3   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   LD_lyso   
4   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   LD_lyso   
5   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   LD_lyso   
6   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   LD_lyso   
7   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
8   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
9   skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
10  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
11  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
12  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
13  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
14  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
15  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
16  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
17  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
18  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
19  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
20  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
21  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
22  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
23  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
24  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
25  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
26  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
27  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
28  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
29  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
30  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
31  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
32  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
33  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
34  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
35  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
36  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
37  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
38  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
39  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
40  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
41  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
42  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
43  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
44  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
45  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
46  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
47  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
48  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...  ER_golgi   
49  skel

In [23]:
contact_counts_df

dataset                                         image_name  \
0     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
1     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
2     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
3     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
4     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
...           ...                                                ...   
5616  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5617  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5618  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5619  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5620  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   

                        object              label    volume  
0                        LD_ER               55_1  0.002532  
1                        LD_ER               55_1  0.002532  
2                        LD_ER              113_1  0.010126  
3                      LD_lyso               55_5  0.199998  
4                      LD_lyso               68_5  0.002532  
...                        ...                ...       ...  
5616  ER_golgi_lyso_mito_perox     1_30_5_226_316  0.002532  
5617  ER_golgi_lyso_mito_perox       1_9_5_13_381  0.010126  
5618  ER_golgi_lyso_mito_perox     1_33_5_186_393  0.002532  
5619  ER_golgi_lyso_mito_perox    1_129_5_259_399  0.005063  
5620  ER_golgi_lyso_mito_perox  1_211_431_375_688  0.007595  

[5621 rows x 5 columns]

In [25]:
contact_counts_df["object"].str.split('_', expand=True)

0      1     2     3      4
0     LD     ER  None  None   None
1     LD     ER  None  None   None
2     LD     ER  None  None   None
3     LD   lyso  None  None   None
4     LD   lyso  None  None   None
...   ..    ...   ...   ...    ...
5616  ER  golgi  lyso  mito  perox
5617  ER  golgi  lyso  mito  perox
5618  ER  golgi  lyso  mito  perox
5619  ER  golgi  lyso  mito  perox
5620  ER  golgi  lyso  mito  perox

[5621 rows x 5 columns]

In [38]:
label_col_len = contact_counts_df["label"].str.split('_', expand=True).shape[1]

In [36]:
[f"org{chr(65 + i)}" for i in range(label_col_len)]

['orgA', 'orgB', 'orgC', 'orgD', 'orgE']

In [37]:
[f"{chr(65 + i)}_ID" for i in range(label_col_len)]

['A_ID', 'B_ID', 'C_ID', 'D_ID', 'E_ID']

In [43]:
contact_counts_df = contacts_df[["dataset", "image_name", "object", "label", "volume"]]

# TODO: include these lables in the original datatable when quantifying to make this function simpler
# contact_counts_df[["orgA", "orgB"]] = contact_counts_df["object"].str.split('_', expand=True)
contact_counts_df[[f"org{chr(65 + i)}" for i in range(label_col_len)]] = contact_counts_df["object"].str.split('_', expand=True)
# contact_counts_df[["A_ID", "B_ID"]] = contact_counts_df["label"].str.split('_', expand=True)
contact_counts_df[[f"{chr(65 + i)}_ID" for i in range(label_col_len)]] = contact_counts_df["label"].str.split('_', expand=True)
for i in range(label_col_len):
    contact_counts_df[chr(65 + i)] = contact_counts_df[f"org{chr(65 + i)}"] +"_" + contact_counts_df[f"{chr(65 + i)}_ID"].astype(str)
# contact_counts_df["A"] = contact_counts_df["orgA"] +"_" + contact_counts_df["A_ID"].astype(str)
# contact_counts_df["B"] = contact_counts_df["orgB"] +"_" + contact_counts_df["B_ID"].astype(str)

C:\Users\redre\AppData\Local\Temp\ipykernel_10764\440758935.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  contact_counts_df[[f"org{chr(65 + i)}" for i in range(label_col_len)]] = contact_counts_df["object"].str.split('_', expand=True)
C:\Users\redre\AppData\Local\Temp\ipykernel_10764\440758935.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  contact_counts_df[[f"org{chr(65 + i)}" for i in range(label_col_len)]] = contact_counts_df["object"].str.split('_', expand=True)
C:\Users\redre\AppData\Local\T

In [44]:
contact_counts_df

dataset                                         image_name  \
0     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
1     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
2     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
3     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
4     skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
...           ...                                                ...   
5616  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5617  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5618  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5619  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   
5620  skel_testa_  05052022_astro_control_1_Linear unmixing_0_cml...   

                        object              label    volume orgA   orgB  orgC  \
0                        LD_ER               55_1  0.002532   LD     ER  None   
1                        LD_ER               55_1  0.002532   LD     ER  None   
2                        LD_ER              113_1  0.010126   LD     ER  None   
3                      LD_lyso               55_5  0.199998   LD   lyso  None   
4                      LD_lyso               68_5  0.002532   LD   lyso  None   
...                        ...                ...       ...  ...    ...   ...   
5616  ER_golgi_lyso_mito_perox     1_30_5_226_316  0.002532   ER  golgi  lyso   
5617  ER_golgi_lyso_mito_perox       1_9_5_13_381  0.010126   ER  golgi  lyso   
5618  ER_golgi_lyso_mito_perox     1_33_5_186_393  0.002532   ER  golgi  lyso   
5619  ER_golgi_lyso_mito_perox    1_129_5_259_399  0.005063   ER  golgi  lyso   
5620  ER_golgi_lyso_mito_perox  1_211_431_375_688  0.007595   ER  golgi  lyso   

      orgD   orgE A_ID B_ID  C_ID  D_ID  E_ID       A          B         C  \
0     None   None   55    1  None  None  None   LD_55       ER_1       NaN   
1     None   None   55    1  None  None  None   LD_55       ER_1       NaN   
2     None   None  113    1  None  None  None  LD_113       ER_1       NaN   
3     None   None   55    5  None  None  None   LD_55     lyso_5       NaN   
4     None   None   68    5  None  None  None   LD_68     lyso_5       NaN   
...    ...    ...  ...  ...   ...   ...   ...     ...        ...       ...   
5616  mito  perox    1   30     5   226   316    ER_1   golgi_30    lyso_5   
5617  mito  perox    1    9     5    13   381    ER_1    golgi_9    lyso_5   
5618  mito  perox    1   33     5   186   393    ER_1   golgi_33    lyso_5   
5619  mito  perox    1  129     5   259   399    ER_1  golgi_129    lyso_5   
5620  mito  perox    1  211   431   375   688    ER_1  golgi_211  lyso_431   

             D          E  
0          NaN        NaN  
1          NaN        NaN  
2          NaN        NaN  
3          NaN        NaN  
4          NaN        NaN  
...        ...        ...  
5616  mito_226  perox_316  
5617   mito_13  perox_381  
5618  mito_186  perox_393  
5619  mito_259  perox_399  
5620  mito_375  perox_688  

[5621 rows x 20 columns]

In [ ]:
content_list = []

In [45]:
unstackedX
contacts_perorgA_percell = contact_counts_df[["dataset", "image_name", "orgA", "A_ID", "object", "volume"]].groupby(["dataset", "image_name", "orgA", "A_ID", "object"]).agg(["count", "sum"])

contacts_perorgA_percell.columns = ["_".join(col_name).rstrip('_') for col_name in contacts_perorgA_percell.columns.to_flat_index()]

unstacked = contacts_perorgA_percell.unstack(level='object')
unstacked.columns = ["_".join(col_name).rstrip('_') for col_name in unstacked.columns.to_flat_index()]
unstacked = unstacked.reset_index()

for col in unstacked.columns:
    if col.startswith("volume_count_"):
        newname = col.split("_")[-1] + "_count"
        unstacked.rename(columns={col:newname}, inplace=True)
    if col.startswith("volume_sum_"):
        newname = col.split("_")[-1] + "_volume"
        unstacked.rename(columns={col:newname}, inplace=True)

unstacked.rename(columns={"orgA":"object", "A_ID":"label"}, inplace=True)
unstacked.set_index(['dataset', 'image_name', 'object', 'label'])

golgi_count  \
dataset     image_name                                         object label                
skel_testa_ 05052022_astro_control_1_Linear unmixing_0_cmle... ER     1            259.0   
                                                               LD     113            NaN   
                                                                      55             NaN   
                                                                      68             NaN   
                                                               golgi  1              NaN   
...                                                                                  ...   
                                                               mito   82             NaN   
                                                                      84             NaN   
                                                                      86             NaN   
                                                                      89             NaN   
                                                                      90             NaN   

                                                                             lyso_count  \
dataset     image_name                                         object label               
skel_testa_ 05052022_astro_control_1_Linear unmixing_0_cmle... ER     1           320.0   
                                                               LD     113           NaN   
                                                                      55            NaN   
                                                                      68            NaN   
                                                               golgi  1             NaN   
...                                                                                 ...   
                                                               mito   82            NaN   
                                                                      84            NaN   
                                                                      86            NaN   
                                                                      89            NaN   
                                                                      90            NaN   

                                                                             mito_count  \
dataset     image_name                                         object label               
skel_testa_ 05052022_astro_control_1_Linear unmixing_0_cmle... ER     1            84.0   
                                                               LD     113           NaN   
                                                                      55            NaN   
                                                                      68            NaN   
                                                               golgi  1             NaN   
...                                                                                 ...   
                                                               mito   82            NaN   
                                                                      84            NaN   
                                                                      86            NaN   
                                                                      89            NaN   
                                                                      90            NaN   

                                                                             perox_count  \
dataset     image_name                                         object label                
skel_testa_ 05052022_astro_control_1_Linear unmixing_0_cmle... ER     1             10.0   
                                                               LD     113            NaN   
                                                                      55             NaN   
                                                    

In [42]:
# now do it again for the opposite organelle
contacts_perorgB_percell = contact_counts_df[["dataset", "image_name", "orgB", "B_ID", "object", "volume"]].groupby(["dataset", "image_name", "orgB", "B_ID", "object"]).agg(["count", "sum"])

contacts_perorgB_percell.columns = ["_".join(col_name).rstrip('_') for col_name in contacts_perorgB_percell.columns.to_flat_index()]

unstackedB = contacts_perorgB_percell.unstack(level='object')
unstackedB.columns = ["_".join(col_name).rstrip('_') for col_name in unstackedB.columns.to_flat_index()]
unstackedB = unstackedB.reset_index()

for col in unstackedB.columns:
    if col.startswith("volume_count_"):
        newname = col.split("_")[-1] + "_count"
        unstackedB.rename(columns={col:newname}, inplace=True)
    if col.startswith("volume_sum_"):
        newname = col.split("_")[-1] + "_volume"
        unstackedB.rename(columns={col:newname}, inplace=True)

unstackedB.rename(columns={"orgB":"object", "B_ID":"label"}, inplace=True)
unstackedB.set_index(['dataset', 'image_name', 'object', 'label'])

ERXLD_count   
dataset        image_name                            object label                
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER     1              NaN  \
                                                     LD     17             1.0   
                                                            2             13.0   
                                                            20             NaN   
                                                            21             1.0   
...                                                                        ...   
               a48hrs-Ctrl_9_Unmixing                perox  79             NaN   
                                                            81             NaN   
                                                            88             NaN   
                                                            9              NaN   
                                                            93             NaN   

                                                                   golgiXER_count   
dataset        image_name                            object label                   
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER     1                33.0  \
                                                     LD     17                NaN   
                                                            2                 NaN   
                                                            20                NaN   
                                                            21                NaN   
...                                                                           ...   
               a48hrs-Ctrl_9_Unmixing                perox  79                NaN   
                                                            81                NaN   
                                                            88                NaN   
                                                            9                 NaN   
                                                            93                NaN   

                                                                   golgiXLD_count   
dataset        image_name                            object label                   
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER     1                 NaN  \
                                                     LD     17                NaN   
                                                            2                 2.0   
                                                            20                NaN   
                                                            21                NaN   
...                                                                           ...   
               a48hrs-Ctrl_9_Unmixing                perox  79                NaN   
                                                            81                NaN   
                                                            88                NaN   
                                                            9                 NaN   
                                                            93                NaN   

                                                                   golgiXperox_count   
dataset        image_name                            object label                      
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER     1                    NaN  \
                                                     LD     17                   NaN   
                                                            2                    NaN   
                                                            20                   NaN   
                                                            21                   NaN   
...                                                                              ...   
               a48hrs-Ctrl_9_Unmixing                perox  79                   NaN

In [43]:
cont_merge = pd.concat([unstacked, unstackedB], axis=0).sort_index(axis=0)
cont_merge=cont_merge.groupby(['dataset', 'image_name', 'object', 'label']).sum().reset_index()

cont_merge

dataset                             image_name object label   
0     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     ER     1  \
1     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD    17   
2     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD     2   
3     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD    20   
4     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD    21   
...              ...                                    ...    ...   ...   
2335  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox    92   
2336  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox    93   
2337  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox    94   
2338  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox    97   
2339  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox    98   

      ERXLD_count  golgiXER_count  golgiXLD_count  golgiXperox_count   
0            49.0            33.0             0.0                0.0  \
1             1.0             0.0             0.0                0.0   
2            13.0             0.0             2.0                0.0   
3             0.0             0.0             0.0                0.0   
4             1.0             0.0             0.0                0.0   
...           ...             ...             ...                ...   
2335          0.0             0.0             0.0                0.0   
2336          0.0             0.0             0.0                0.0   
2337          0.0             0.0             0.0                0.0   
2338          0.0             0.0             0.0                0.0   
2339          0.0             0.0             0.0                0.0   

      lysoXER_count  lysoXLD_count  lysoXgolgi_count  lysoXmito_count   
0             130.0            0.0               0.0              0.0  \
1               0.0            0.0               0.0              0.0   
2               0.0            0.0               0.0              0.0   
3               0.0            0.0               0.0              0.0   
4               0.0            0.0               0.0              0.0   
...             ...            ...               ...              ...   
2335            0.0            0.0               0.0              0.0   
2336            0.0            0.0               0.0              0.0   
2337            0.0            0.0               0.0              0.0   
2338            0.0            0.0               0.0              0.0   
2339            0.0            0.0               0.0              0.0   

      lysoXperox_count  mitoXER_count  mitoXLD_count  mitoXgolgi_count   
0                  0.0          129.0            0.0               0.0  \
1                  0.0            0.0            0.0               0.0   
2                  0.0            0.0            4.0               0.0   
3                  0.0            0.0            1.0               0.0   
4                  0.0            0.0            0.0               0.0   
...                ...            ...            ...               ...   
2335               0.0            0.0            0.0               0.0   
2336               0.0            0.0            0.0               0.0   
2337               0.0            0.0            0.0               0.0   
2338               0.0            0.0            0.0               0.0   
2339               0.0            0.0            0.0               0.0   

      mitoXperox_count  peroxXER_count  peroxXLD_count  ERXLD_volume   
0                  0.0           123.0             0.0      9.418127  \
1                  0.0             0.0             0.0      0.211002   
2                  0.0             0.0             4.0      6.466584   
3                  0.0             0.0             0.0      0.000000   
4                  0.0             0.0             0.0      0.047165   
...                ...             ..

In [44]:
# confirming the two dataframes have the same datatimes in the indexes
org_df['dataset']=org_df['dataset'].astype(str)
org_df['image_name']=org_df['image_name'].astype(str)
org_df['object']=org_df['object'].astype(str)
org_df['label']=org_df['label'].astype("Int64")

cont_merge['dataset']=cont_merge['dataset'].astype(str)
cont_merge['image_name']=cont_merge['image_name'].astype(str)
cont_merge['object']=cont_merge['object'].astype(str)
cont_merge['label']=cont_merge['label'].astype("Int64")

In [45]:
# important to ensure all organelles not in contact were filled with 0
combo_test = pd.merge(org_df, cont_merge, how='left', on=['dataset', 'image_name', 'object', 'label'], sort=True)
combo_test[cont_merge.columns]=combo_test[cont_merge.columns].fillna(0)
combo_test

dataset                             image_name object  label   
0     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     ER      1  \
1     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD      2   
2     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD      5   
3     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD      8   
4     20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     LD      9   
...              ...                                    ...    ...    ...   
3494  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox     95   
3495  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox     96   
3496  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox     97   
3497  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox     98   
3498  20231101_testa                 a48hrs-Ctrl_9_Unmixing  perox     99   

                         scale  centroid-0  centroid-1  centroid-2  bbox-0   
0     (0.3891, 0.0799, 0.0799)    2.360129   35.230569   27.932606       2  \
1     (0.3891, 0.0799, 0.0799)    1.580787   35.089615   39.045027       2   
2     (0.3891, 0.0799, 0.0799)    0.904617   30.858447   41.395361       2   
3     (0.3891, 0.0799, 0.0799)    0.996353   41.008183   50.610690       2   
4     (0.3891, 0.0799, 0.0799)    0.778237   45.033841   56.012062       2   
...                        ...         ...         ...         ...     ...   
3494  (0.3891, 0.0799, 0.0799)    5.188247   25.758608   18.077617      13   
3495  (0.3891, 0.0799, 0.0799)    5.169717   27.156362   18.895351      13   
3496  (0.3891, 0.0799, 0.0799)    5.058540   29.073281   20.310220      13   
3497  (0.3891, 0.0799, 0.0799)    5.836777   13.278662   27.875206      15   
3498  (0.3891, 0.0799, 0.0799)    5.836777   26.341671   26.477453      15   

      bbox-1  bbox-2  bbox-3  bbox-4  bbox-5  surface_area      volume   
0          4       0      12     704     701   6229.786939  879.529900  \
1        378     452       9     478     516     76.705775   17.520595   
2        379     512       4     392     525      4.539345    0.290438   
3        507     626       4     520     641      5.431245    0.553569   
4        561     699       3     568     704      1.111749    0.071989   
...      ...     ...     ...     ...     ...           ...         ...   
3494     321     225      15     325     229      1.152902    0.044683   
3495     339     235      15     343     239      1.078354    0.034753   
3496     363     253      14     366     256      0.647406    0.017377   
3497     166     348      16     168     351      0.494978    0.009929   
3498     329     330      16     332     334      0.799834    0.024824   

      SA_to_volume_ratio  equivalent_diameter    extent  euler_number   
0               7.083087            11.887321  0.072205          -710  \
1               4.378035             3.222429  0.157545             1   
2              15.629322             0.821646  0.346154             0   
3               9.811317             1.018727  0.571795             1   
4              15.443355             0.516126  0.828571             1   
...                  ...                  ...       ...           ...   
3494           25.801964             0.440265  0.562500             1   
3495           31.028894             0.404885  0.437500             1   
3496           37.257325             0.321358  0.777778             1   
3497           49.849288             0.266671  0.666667             1   
3498           32.220540             0.361929  0.833333             1   

      solidity  axis_major_length  min_intensity  max_intensity   
0     0.179404          54.336667            0.0        36701.0  \
1     0.440574           7.804411         4911.0        40086.0   
2     0.664773           1.230545        13286.0        30306.0   
3     0.877953           1.361856        12930.0        37787.0   
4          inf           0.632459        17696.0  

In [46]:
## OLD CODE TO DO THIS
# column_names = org_df.columns
# for col in column_names:
#     if col.endswith("_labels"):
#         org_df[f"n_{col.split('_')[0]}_contacting"] = org_df[col].map(len, 'ignore')

# for col in column_names:
#     if col.endswith("_overlap"):
#         org_df[f"area_{col.split('_')[0]}_contacting_norm"] = org_df[col].div(org_df["volume"])

# column_names = org_df.columns
# for col in column_names:
#     if col.endswith("_contacting"):
#         org_df[f"n_{col.split('_')[1]}_contacting_norm"] = org_df[col].div(org_df["volume"])

____________________
## 3. Summary stats for organelle and contact sites metrics per cell

#### Organelles: volume sum and count

In [47]:
group_by = ['dataset', "image_name", "object"]

stats1 = org_df[group_by + ["volume"]].groupby(group_by).agg(["count", "sum", "mean", "median", "std"])
stats1

volume   
                                                             count   
dataset        image_name                            object          
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER          1  \
                                                     LD         44   
                                                     golgi       5   
                                                     lyso       74   
                                                     mito        4   
...                                                            ...   
               a48hrs-Ctrl_9_Unmixing                LD          1   
                                                     golgi       3   
                                                     lyso      307   
                                                     mito        4   
                                                     perox      96   

                                                                          
                                                                    sum   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD       27.852235   
                                                     golgi    47.892440   
                                                     lyso     90.365857   
                                                     mito    307.653011   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    31.769421   
                                                     lyso    104.637025   
                                                     mito    301.789643   
                                                     perox     8.827322   

                                                                          
                                                                   mean   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.633005   
                                                     golgi     9.578488   
                                                     lyso      1.221160   
                                                     mito     76.913253   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    10.589807   
                                                     lyso      0.340837   
                                                     mito     75.447411   
                                                     perox     0.091951   

                                                                          
                                                                 median   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.171284   
                                                     golgi     2.206830   
                                                     lyso      0.148942   
                                                     mito      3.888639   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi     7.534005   
                                                     lyso      0.071989   
                                                     mito      6.534849   
  

#### Organelles: surface area sum

In [48]:
stats2 = org_df[group_by + ["surface_area"]].groupby(group_by).agg(["sum", "mean", "median", "std"])
stats2

surface_area   
                                                                     sum   
dataset        image_name                            object                
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      6229.786939  \
                                                     LD       208.258637   
                                                     golgi    240.748239   
                                                     lyso     648.248123   
                                                     mito    2103.707968   
...                                                                  ...   
               a48hrs-Ctrl_9_Unmixing                LD         2.856486   
                                                     golgi    198.755819   
                                                     lyso    1935.193611   
                                                     mito    2073.072974   
                                                     perox    169.058559   

                                                                           
                                                                    mean   
dataset        image_name                            object                
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      6229.786939  \
                                                     LD         4.733151   
                                                     golgi     48.149648   
                                                     lyso       8.760110   
                                                     mito     525.926992   
...                                                                  ...   
               a48hrs-Ctrl_9_Unmixing                LD         2.856486   
                                                     golgi     66.251940   
                                                     lyso       6.303562   
                                                     mito     518.268244   
                                                     perox      1.761027   

                                                                           
                                                                  median   
dataset        image_name                            object                
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      6229.786939  \
                                                     LD         2.539323   
                                                     golgi     18.486606   
                                                     lyso       2.685393   
                                                     mito      31.959143   
...                                                                  ...   
               a48hrs-Ctrl_9_Unmixing                LD         2.856486   
                                                     golgi     55.003118   
                                                     lyso       1.663463   
                                                     mito      48.132400   
                                                     perox      1.441795   

                                                                          
                                                                     std  
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER              NaN  
                                                     LD        11.313982  
                                                     golgi     54.576199  
                                                     lyso      27.709532  
                                                     mito    1005.246977  
...                                                                  ...  
               a48hrs-Ctrl_9_Unmixing                LD              NaN  
                                                     golgi     57.185396  
                                        

####  Organelles: mean, median, standard deviation

In [49]:
statcolumns = ['dataset',"image_name", "object", "SA_to_volume_ratio", "equivalent_diameter", 
                 "extent", "euler_number", "solidity", "axis_major_length"]

stats3 = org_df[statcolumns].groupby(group_by).agg(["mean", "median", "std"])
stats3

SA_to_volume_ratio   
                                                                          mean   
dataset        image_name                            object                      
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER               7.083087  \
                                                     LD              17.056840   
                                                     golgi            8.103251   
                                                     lyso            17.352583   
                                                     mito            13.319618   
...                                                                        ...   
               a48hrs-Ctrl_9_Unmixing                LD              14.383841   
                                                     golgi            7.079242   
                                                     lyso            23.575560   
                                                     mito             9.487678   
                                                     perox           24.799139   

                                                                         
                                                                median   
dataset        image_name                            object              
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER       7.083087  \
                                                     LD      15.858851   
                                                     golgi    7.405898   
                                                     lyso    17.993606   
                                                     mito    12.592802   
...                                                                ...   
               a48hrs-Ctrl_9_Unmixing                LD      14.383841   
                                                     golgi    7.300648   
                                                     lyso    23.297003   
                                                     mito     7.426834   
                                                     perox   23.400471   

                                                                        
                                                                  std   
dataset        image_name                            object             
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER           NaN  \
                                                     LD      6.458695   
                                                     golgi   4.207923   
                                                     lyso    7.050112   
                                                     mito    7.223941   
...                                                               ...   
               a48hrs-Ctrl_9_Unmixing                LD           NaN   
                                                     golgi   1.244013   
                                                     lyso    4.412596   
                                                     mito    4.539660   
                                                     perox   7.922695   

                                                            equivalent_diameter   
                                                                           mean   
dataset        image_name                            object                       
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER               11.887321  \
                                                     LD                0.753673   
                                                     golgi             2.156453   
                                                     lyso              0.863850   
                                                     mito              3.118793   
...                                                                         ...   
               a48hrs-Ctrl_9_Unmixing                LD                0.723857   
                     

#### Organelles: mean , median, std of contacts

In [50]:
statscolumns1 = [col for col in combo_test.columns if col.endswith(("_count", "_volume"))]

contact_cnts_stats = combo_test[group_by + statscolumns1].groupby(group_by).agg(['sum', 'mean', 'median', 'std'])
contact_cnts_stats

ERXLD_count   
                                                                    sum   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER            49.0  \
                                                     LD            49.0   
                                                     golgi          0.0   
                                                     lyso           0.0   
                                                     mito           0.0   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD             1.0   
                                                     golgi          0.0   
                                                     lyso           0.0   
                                                     mito           0.0   
                                                     perox          0.0   

                                                                                
                                                                  mean median   
dataset        image_name                            object                     
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      49.000000   49.0  \
                                                     LD       1.113636    1.0   
                                                     golgi    0.000000    0.0   
                                                     lyso     0.000000    0.0   
                                                     mito     0.000000    0.0   
...                                                                ...    ...   
               a48hrs-Ctrl_9_Unmixing                LD       1.000000    1.0   
                                                     golgi    0.000000    0.0   
                                                     lyso     0.000000    0.0   
                                                     mito     0.000000    0.0   
                                                     perox    0.000000    0.0   

                                                                        
                                                                  std   
dataset        image_name                            object             
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER           NaN  \
                                                     LD      1.955504   
                                                     golgi   0.000000   
                                                     lyso    0.000000   
                                                     mito    0.000000   
...                                                               ...   
               a48hrs-Ctrl_9_Unmixing                LD           NaN   
                                                     golgi   0.000000   
                                                     lyso    0.000000   
                                                     mito    0.000000   
                                                     perox   0.000000   

                                                            golgiXER_count   
                                                                       sum   
dataset        image_name                            object                  
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER               33.0  \
                                                     LD                0.0   
                                                     golgi            33.0   
                                                     lyso              0.0   
                                                     mito              0.0   
...                                                                    ...   
               a48hrs-Ctrl_9_Unmixing                LD                0.0   
                                                     golgi            4

#### Organelles: Combine summary stats into one new dataframe

In [51]:
org_merge_1= pd.merge(stats1, stats2, 'outer', left_on=group_by, right_index=True)
org_merge_2 = pd.merge(org_merge_1, stats3, 'outer', left_on=group_by, right_index=True)
org_merge_3 = pd.merge(org_merge_2, contact_cnts_stats, 'outer', left_on=group_by, right_index=True)

org_merge_3

volume   
                                                             count   
dataset        image_name                            object          
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER          1  \
                                                     LD         44   
                                                     golgi       5   
                                                     lyso       74   
                                                     mito        4   
...                                                            ...   
               a48hrs-Ctrl_9_Unmixing                LD          1   
                                                     golgi       3   
                                                     lyso      307   
                                                     mito        4   
                                                     perox      96   

                                                                          
                                                                    sum   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD       27.852235   
                                                     golgi    47.892440   
                                                     lyso     90.365857   
                                                     mito    307.653011   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    31.769421   
                                                     lyso    104.637025   
                                                     mito    301.789643   
                                                     perox     8.827322   

                                                                          
                                                                   mean   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.633005   
                                                     golgi     9.578488   
                                                     lyso      1.221160   
                                                     mito     76.913253   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    10.589807   
                                                     lyso      0.340837   
                                                     mito     75.447411   
                                                     perox     0.091951   

                                                                          
                                                                 median   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.171284   
                                                     golgi     2.206830   
                                                     lyso      0.148942   
                                                     mito      3.888639   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi     7.534005   
                                                     lyso      0.071989   
                                                     mito      6.534849   
  

#### Contacts: mean, median, standard deviation

In [52]:
contact_1 = contacts_df[group_by +['volume']].groupby(group_by).agg(["count", "sum", "mean", "median", "std"])
contact_2 = contacts_df[group_by +['surface_area']].groupby(group_by).agg(["sum", "mean", "median", "std"])
contact_3 = contacts_df[statcolumns].groupby(group_by).agg(["mean", "median", "std"])

contact_merged_1 = pd.merge(contact_1, contact_2, 'outer', left_on=group_by, right_index=True)
contact_merged_2 = pd.merge(contact_merged_1, contact_3, 'outer', left_on=group_by, right_index=True)
contact_merged_2

volume   
                                                                  count   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD           49  \
                                                     golgiXER        33   
                                                     golgiXLD         4   
                                                     golgiXperox      3   
                                                     lysoXER        130   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox      11   
                                                     mitoXER        170   
                                                     mitoXgolgi      30   
                                                     mitoXperox      32   
                                                     peroxXER        93   

                                                                              
                                                                        sum   
dataset        image_name                            object                   
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD         9.418127  \
                                                     golgiXER     17.959975   
                                                     golgiXLD      0.181213   
                                                     golgiXperox   0.059577   
                                                     lysoXER      31.464089   
...                                                                     ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox    0.193625   
                                                     mitoXER      89.596322   
                                                     mitoXgolgi    4.825735   
                                                     mitoXperox    0.739747   
                                                     peroxXER      4.498062   

                                                                             
                                                                      mean   
dataset        image_name                            object                  
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD        0.192207  \
                                                     golgiXER     0.544242   
                                                     golgiXLD     0.045303   
                                                     golgiXperox  0.019859   
                                                     lysoXER      0.242031   
...                                                                    ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox   0.017602   
                                                     mitoXER      0.527037   
                                                     mitoXgolgi   0.160858   
                                                     mitoXperox   0.023117   
                                                     peroxXER     0.048366   

                                                                             
                                                                    median   
dataset        image_name                            object                  
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD        0.042200  \
                                                     golgiXER     0.024824   
                                                     golgiXLD     0.014894   
                                                     golgiXperox  0.009929   
                                                     lysoXER      0.037236   
...                                                                    ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox   0.012412   
                                  

____________________
## 4. Summary stats for XY and Z distributions

#### Distribution: histogram summary stats per organelle per cell

In [53]:
dtest_selet = dist_df.loc[[dist_df.index[0]]]
dtest_selet

dataset                             image_name object   
0  20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing   lyso  \

                      scale  XY_n_bins          XY_bins   
0  (0.3891, 0.0799, 0.0799)          5  [1, 2, 3, 4, 5]  \

                     XY_mask_vox_cnt_perbin            XY_obj_vox_cnt_perbin   
0  [386342, 138548, 217246, 309808, 333312]  [673, 2684, 15554, 15636, 1856]  \

  XY_center_vox_cnt_perbin                                XY_n_pix_perbin   
0     [261616, 0, 0, 0, 0]  [38635.0, 13866.0, 22879.0, 40149.0, 87468.0]  \

                               XY_portion_pix_perbin  XY_n_wedges   
0  [0.19032300969965074, 0.06830642817381538, 0.1...            8  \

                  XY_wedges   
0  [1, 2, 3, 4, 5, 6, 7, 8]  \

                            XY_mask_vox_cnt_perwedge   
0  [102969, 60039, 169532, 382361, 189714, 115593...  \

                       XY_obj_vox_cnt_perwedge   
0  [400, 207, 419, 12666, 193, 570, 86, 21862]  \

                          XY_center_vox_cnt_perwedge   
0  [36143, 26204, 31728, 40590, 32046, 35745, 223...  \

                                   XY_n_pix_perwedge   
0  [12633.0, 6551.0, 29455.0, 60630.0, 27588.0, 1...  \

                             XY_portion_pix_perwedge   
0  [0.062232446784927856, 0.03227141287802283, 0....  \

                                    XY_wedges_perbin   
0  [[1, 2, 3, 4, 5, 6, 7, 8], [1, 2, 3, 4, 5, 6, ...  \

                       XY_mask_vox_cnt_wedges_perbin   
0  [[52980, 39830, 48620, 53200, 55040, 50552, 38...  \

                        XY_obj_vox_cnt_wedges_perbin   
0  [[16, 0, 65, 276, 24, 204, 69, 19], [164, 0, 1...  \

                     XY_center_vox_cnt_wedges_perbin   
0  [[36143, 26204, 31728, 40590, 32046, 35745, 22...  \

                              XY_n_pix_wedges_perbin   
0  [[5298.0, 3983.0, 4862.0, 5320.0, 5504.0, 5056...  \

                                   XY_mask_cv_perbin   
0  [5.232997707758694e-05, 0.002281382012497204, ...  \

                                    XY_obj_cv_perbin   
0  [1.0679460760597017, 1.125253293749041, 1.6236...  \

                         XY_center_cv_perbin   
0  [0.10401044371083833, 0.0, 0.0, 0.0, 0.0]  \

                                  XY_mask_vol_perbin   
0  [959.04530107129, 343.9279404590365, 539.28580...  \

                                   XY_obj_vol_perbin   
0  [1.6706376413151514, 6.66269157398197, 38.6108...  \

                      XY_center_vol_perbin   
0  [649.4287327939147, 0.0, 0.0, 0.0, 0.0]  \

                                XY_mask_vol_perwedge   
0  [255.60755912121815, 149.03924717224422, 420.8...  \

                                 XY_obj_vol_perwedge   
0  [0.9929495639317393, 0.513851399334675, 1.0401...  \

                              XY_center_vol_perwedge   
0  [89.72044022296213, 65.04812593316824, 78.7607...  \

                           XY_mask_vol_wedges_perbin   
0  [[131.51616974275888, 98.87295282850293, 120.6...  \

                            XY_obj_vol_wedges_perbin   
0  [[0.03971798255726957, 0.0, 0.1613543041389076...  \

                         XY_center_vol_wedges_perbin   
0  [[89.72044022296213, 65.04812593316824, 78.760...  \

                                      XY_area_perbin   
0  [246.4712395098411, 88.45788034278391, 145.956...  \

                                    XY_area_perwedge   
0  [80.59198055462204, 41.79197851763864, 187.907...  \

                               XY_area_wedges_perbin   
0  [[33.79848911409701, 25.409471902878142, 31.01...  \

                                           zernike_n   
0  [0, 1, 2, 2, 3, 3, 4, 4, 4, 5, 5, 5, 6, 6, 6, ...  \

                                           zernike_m   
0  [0, 1, 0, 2, 1, 3, 0, 2, 4, 1, 3, 5, 0, 2, 4, ...  \

                                    zernike_mask_mag   
0  [1.0, 0.2770483979997788, 0.5461988487672376, ...  \

                                    zernike_mask_phs   
0  [1.5707963267948966, -0.12479380508422404, -1....  \

         

In [54]:
tesT_bins_df = dtest_selet[['Z_slices', 'Z_mask_vox_cnt', 'Z_obj_vox_cnt']]
tesT_bins_df_B = dtest_selet[['XY_wedges', 'XY_mask_vox_cnt_perwedge', 'XY_obj_vox_cnt_perwedge']]
tesT_bins_df_C = dtest_selet[['XY_bins', 'XY_mask_vox_cnt_perbin', 'XY_obj_vox_cnt_perbin']]

tesT_bins_df

Z_slices   
0  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,...  \

                                      Z_mask_vox_cnt   
0  [0, 0, 162424, 163166, 153092, 146649, 133633,...  \

                                       Z_obj_vox_cnt  
0  [0, 0, 1043, 2044, 3467, 4510, 4813, 5014, 503...

In [55]:
group_by = ["dataset", "image_name", "object"]

indexes_test = dtest_selet[group_by]
indexes_test

dataset                             image_name object
0  20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing   lyso

In [56]:
# creating dataframe to construct the histogram; for Z slices, the histogram bins are normalized into 10 bins
test_bins = tesT_bins_df["Z_slices"].values[0][1:-1].split(", ")
test_org = tesT_bins_df["Z_mask_vox_cnt"].values[0][1:-1].split(", ")
test_mask = tesT_bins_df["Z_obj_vox_cnt"].values[0][1:-1].split(", ")

test_single_df = pd.DataFrame(list(zip(test_bins, test_org, test_mask)), columns =['bins', 'org_hist', 'cell_hist']).astype(int)
test_single_df['normed_org_hist'] = (test_single_df.org_hist/test_single_df.cell_hist).fillna(0)
test_single_df['normed_bins'] = (test_single_df.bins/max(test_single_df.bins)*10).apply(np.floor)
test_single_df

bins  org_hist  cell_hist  normed_org_hist  normed_bins
0      0         0          0         0.000000          0.0
1      1         0          0         0.000000          0.0
2      2    162424       1043       155.727709          1.0
3      3    163166       2044        79.826810          1.0
4      4    153092       3467        44.156908          2.0
5      5    146649       4510        32.516408          3.0
6      6    133633       4813        27.765011          3.0
7      7    128056       5014        25.539689          4.0
8      8    127195       5034        25.267183          5.0
9      9    123573       4533        27.260754          5.0
10    10    124375       3497        35.566200          6.0
11    11    123093       2448        50.283088          6.0
12    12         0          0         0.000000          7.0
13    13         0          0         0.000000          8.0
14    14         0          0         0.000000          8.0
15    15         0          0         0.000000          9.0
16    16         0          0         0.000000         10.0

In [57]:
# creating histogram
test_s = test_single_df['normed_bins'].repeat(test_single_df['normed_org_hist'])

# example summary stat
test_s.mode()[0]

1.0

In [58]:
# create dataframe to collect summary stats for each cell
test_tab = pd.DataFrame(dtest_selet[['dataset', 'image_name', 'object']])
test_tab

dataset                             image_name object
0  20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing   lyso

In [59]:
# collecting summary stats
test_tab['hist_mean']=[test_s.mean()]
test_tab['hist_median']=[test_s.median()]
if test_single_df['org_hist'].sum() != 0: test_tab['hist_mode']=[test_s.mode()[0]]
else: test_tab['hist_mode']=['NaN']
test_tab['hist_min']=[test_s.min()]
test_tab['hist_max']=[test_s.max()]
test_tab['hist_range']=[test_s.max() - test_s.min()]
test_tab['hist_stdev']=[test_s.std()]
test_tab['hist_skew']=[test_s.skew()]
test_tab['hist_kurtosis']=[test_s.kurtosis()]
test_tab['hist_var']=[test_s.var()]

# renaming the summary stats to indicate which distribution they are describing
test_prefix = "Z_slices_obj_"
test_tab.columns = [test_prefix+col for col in test_tab.columns]
test_tab

test_tab

Z_slices_obj_dataset                Z_slices_obj_image_name   
0       20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing  \

  Z_slices_obj_object  Z_slices_obj_hist_mean  Z_slices_obj_hist_median   
0                lyso                2.743487                       2.0  \

   Z_slices_obj_hist_mode  Z_slices_obj_hist_min  Z_slices_obj_hist_max   
0                     1.0                    1.0                    6.0  \

   Z_slices_obj_hist_range  Z_slices_obj_hist_stdev  Z_slices_obj_hist_skew   
0                      5.0                 1.976349                  0.6073  \

   Z_slices_obj_hist_kurtosis  Z_slices_obj_hist_var  
0                   -1.266961               3.905956

In [60]:
# create a for loop to process data for each type of distribution
hist_dfs = []
for ind in dist_df.index:
    selection = dist_df.loc[[ind]]
    bins_df = pd.DataFrame()
    wedges_df = pd.DataFrame()
    Z_df = pd.DataFrame()

    bins_df[['bins', 'masks', 'obj']] = selection[['XY_bins', 'XY_mask_vox_cnt_perbin', 'XY_obj_vox_cnt_perbin']]
    wedges_df[['bins', 'masks', 'obj']] = selection[['XY_wedges', 'XY_mask_vox_cnt_perwedge', 'XY_obj_vox_cnt_perwedge']]
    Z_df[['bins', 'masks', 'obj']] = selection[['Z_slices', 'Z_mask_vox_cnt', 'Z_obj_vox_cnt']]

    dfs = [selection[['dataset', 'image_name', 'object']].reset_index()]
    for df, prefix in zip([bins_df, wedges_df, Z_df], ["XY_bins_", "XY_wedges_", "Z_slices_"]):
        single_df = pd.DataFrame(list(zip(df["bins"].values[0][1:-1].split(", "), 
                                          df["obj"].values[0][1:-1].split(", "), 
                                          df["masks"].values[0][1:-1].split(", "))), columns =['bins', 'obj', 'mask']).astype(int)
        
        single_df['mask_fract'] = single_df['mask']/single_df['mask'].max()
        single_df['obj_norm'] = (single_df["obj"]/single_df["mask_fract"]).fillna(0)
        single_df['portion_per_bin'] = (single_df["obj"] / single_df["obj"].sum())*100

        if "Z_" in prefix:
            single_df['bins'] = (single_df["bins"]/max(single_df.bins)*10).apply(np.floor)

        sumstats_df = pd.DataFrame()

        s = single_df['bins'].repeat(single_df['obj_norm'])
        sumstats_df['hist_mean']=[s.mean()]
        sumstats_df['hist_median']=[s.median()]
        if single_df['obj_norm'].sum() != 0: sumstats_df['hist_mode']=[s.mode()[0]]
        else: sumstats_df['hist_mode']=['NaN']
        sumstats_df['hist_min']=[s.min()]
        sumstats_df['hist_max']=[s.max()]
        sumstats_df['hist_range']=[s.max() - s.min()]
        sumstats_df['hist_stdev']=[s.std()]
        sumstats_df['hist_skew']=[s.skew()]
        sumstats_df['hist_kurtosis']=[s.kurtosis()]
        sumstats_df['hist_var']=[s.var()]
        sumstats_df.columns = [prefix+col for col in sumstats_df.columns]
        dfs.append(sumstats_df.reset_index())
    combined_df = pd.concat(dfs, axis=1).drop(columns="index")
    hist_dfs.append(combined_df)
hist_df_combo = pd.concat(hist_dfs, ignore_index=True)
hist_df_combo

dataset                             image_name    object   
0    20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing      lyso  \
1    20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing      mito   
2    20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     golgi   
3    20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing     perox   
4    20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing        ER   
..              ...                                    ...       ...   
268  20231101_testa                 a48hrs-Ctrl_9_Unmixing  golgiXER   
269  20231101_testa                 a48hrs-Ctrl_9_Unmixing  golgiXLD   
270  20231101_testa                 a48hrs-Ctrl_9_Unmixing  peroxXER   
271  20231101_testa                 a48hrs-Ctrl_9_Unmixing  peroxXLD   
272  20231101_testa                 a48hrs-Ctrl_9_Unmixing     ERXLD   

     XY_bins_hist_mean  XY_bins_hist_median XY_bins_hist_mode   
0             3.260502                  3.0                 3  \
1             3.159258                  3.0                 2   
2             2.693031                  2.0                 2   
3             3.151505                  3.0                 2   
4             3.110104                  3.0                 2   
..                 ...                  ...               ...   
268           2.882984                  3.0                 3   
269                NaN                  NaN               NaN   
270           3.027207                  3.0                 2   
271                NaN                  NaN               NaN   
272           2.212687                  2.0                 2   

     XY_bins_hist_min  XY_bins_hist_max  XY_bins_hist_range   
0                 1.0               5.0                 4.0  \
1                 1.0               5.0                 4.0   
2                 2.0               5.0                 3.0   
3                 1.0               5.0                 4.0   
4                 1.0               5.0                 4.0   
..                ...               ...                 ...   
268               1.0               5.0                 4.0   
269               NaN               NaN                 NaN   
270               1.0               5.0                 4.0   
271               NaN               NaN                 NaN   
272               2.0               3.0                 1.0   

     XY_bins_hist_stdev  XY_bins_hist_skew  XY_bins_hist_kurtosis   
0              0.773465          -0.152117               0.020488  \
1              1.023845           0.330714              -1.069744   
2              0.786781           0.685490              -0.786982   
3              1.074558           0.228977              -0.998331   
4              1.193585           0.149567              -1.061417   
..                  ...                ...                    ...   
268            0.831572           0.516359              -0.333808   
269                 NaN                NaN                    NaN   
270            1.078032           0.415493              -0.843205   
271                 NaN                NaN                    NaN   
272            0.409973           1.412159              -0.005908   

     XY_bins_hist_var  XY_wedges_hist_mean  XY_wedges_hist_median   
0            0.598247             6.310818                    8.0  \
1            1.048258             5.326824                    5.0   
2            0.619024             4.331279                    4.0   
3            1.154675             4.525333                    5.0   
4            1.424645             4.688464                    5.0   
..                ...                  ...                    ...   
268          0.691512             4.759889                    6.0   
269               NaN                  NaN                    NaN   
270          1.162152             4.087042                    4.0   
271               NaN                  NaN                    NaN   
272          0.168078

#### Distribution: histogram summary stats for the centering object (nucleus) per cell

In [61]:
# collect the centering object columns into a new dataframe
test_unique_tab = dist_df[["dataset", "image_name", 
                      "XY_bins", "XY_center_vox_cnt_perbin", 
                      "XY_wedges", "XY_center_vox_cnt_perwedge",
                      "Z_slices", "Z_center_vox_cnt"]].set_index(["dataset", "image_name"])

In [62]:
# identify the indexes for each unique image 
uniques = test_unique_tab.index.unique()
test_unique_tab.loc[uniques[0]].iloc[[0]].reset_index()

dataset                             image_name          XY_bins   
0  20231101_testa  24hrs-Ctrl +oleicAcid 50uM_2_Unmixing  [1, 2, 3, 4, 5]  \

  XY_center_vox_cnt_perbin                 XY_wedges   
0     [261616, 0, 0, 0, 0]  [1, 2, 3, 4, 5, 6, 7, 8]  \

                          XY_center_vox_cnt_perwedge   
0  [36143, 26204, 31728, 40590, 32046, 35745, 223...  \

                                            Z_slices   
0  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,...  \

                                    Z_center_vox_cnt  
0  [0, 0, 11271, 28253, 34525, 37621, 37884, 3699...

In [63]:
# create a for loop to process data for each type of distribution
nuc_dist_df = dist_df[["dataset", "image_name", 
                      "XY_bins", "XY_center_vox_cnt_perbin", "XY_mask_vox_cnt_perbin",
                      "XY_wedges", "XY_center_vox_cnt_perwedge", "XY_mask_vox_cnt_perwedge",
                      "Z_slices", "Z_center_vox_cnt", "Z_mask_vox_cnt"]].set_index(["dataset", "image_name"])

nuc_hist_dfs = []
for idx in nuc_dist_df.index.unique():
    selection = nuc_dist_df.loc[idx].iloc[[0]].reset_index()
    bins_df = pd.DataFrame()
    wedges_df = pd.DataFrame()
    Z_df = pd.DataFrame()

    bins_df[['bins', 'center', 'masks']] = selection[['XY_bins', 'XY_center_vox_cnt_perbin', 'XY_mask_vox_cnt_perbin']]
    wedges_df[['bins', 'center', 'masks']] = selection[['XY_wedges', 'XY_center_vox_cnt_perwedge', 'XY_mask_vox_cnt_perwedge']]
    Z_df[['bins', 'center', 'masks']] = selection[['Z_slices', 'Z_center_vox_cnt', 'Z_mask_vox_cnt']]

    dfs = [selection[['dataset', 'image_name']]]
    for df, prefix in zip([bins_df, wedges_df, Z_df], ["XY_bins_", "XY_wedges_", "Z_slices_"]):
        single_df = pd.DataFrame(list(zip(df["bins"].values[0][1:-1].split(", "), 
                                          df["masks"].values[0][1:-1].split(", "),
                                          df["center"].values[0][1:-1].split(", "))), columns =['bins', 'mask', 'obj']).astype(int)
        single_df['mask_fract'] = single_df['mask']/single_df['mask'].max()
        single_df['obj_norm'] = (single_df["obj"]/single_df["mask_fract"]).fillna(0)
        single_df['portion_per_bin'] = (single_df["obj"] / single_df["obj"].sum())*100
        if "Z_" in prefix:
            single_df['bins'] = (single_df["bins"]/max(single_df.bins)*10).apply(np.floor)

        sumstats_df = pd.DataFrame()

        s = single_df['bins'].repeat(single_df['obj_norm'])
        sumstats_df['hist_mean']=[s.mean()]
        sumstats_df['hist_median']=[s.median()]
        if single_df['obj_norm'].sum() != 0: sumstats_df['hist_mode']=[s.mode()[0]]
        else: sumstats_df['hist_mode']=['NaN']
        sumstats_df['hist_min']=[s.min()]
        sumstats_df['hist_max']=[s.max()]
        sumstats_df['hist_range']=[s.max() - s.min()]
        sumstats_df['hist_stdev']=[s.std()]
        sumstats_df['hist_skew']=[s.skew()]
        sumstats_df['hist_kurtosis']=[s.kurtosis()]
        sumstats_df['hist_var']=[s.var()]
        sumstats_df.columns = [prefix+col for col in sumstats_df.columns]
        dfs.append(sumstats_df.reset_index())
    combined_df = pd.concat(dfs, axis=1).drop(columns="index")
    nuc_hist_dfs.append(combined_df)
hist_center_df_combo = pd.concat(nuc_hist_dfs, ignore_index=True)
hist_center_df_combo.insert(2, column="object", value="nuc")
hist_center_df_combo.head()

dataset                               image_name object   
0  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_2_Unmixing    nuc  \
1  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_3_Unmixing    nuc   
2  20231101_testa  a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing    nuc   
3  20231101_testa   a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing    nuc   
4  20231101_testa                  a24hrs-Ctrl_10_Unmixing    nuc   

   XY_bins_hist_mean  XY_bins_hist_median  XY_bins_hist_mode   
0                1.0                  1.0                  1  \
1                1.0                  1.0                  1   
2                1.0                  1.0                  1   
3                1.0                  1.0                  1   
4                1.0                  1.0                  1   

   XY_bins_hist_min  XY_bins_hist_max  XY_bins_hist_range  XY_bins_hist_stdev   
0                 1                 1                   0                 0.0  \
1                 1                 1                   0                 0.0   
2                 1                 1                   0                 0.0   
3                 1                 1                   0                 0.0   
4                 1                 1                   0                 0.0   

   XY_bins_hist_skew  XY_bins_hist_kurtosis  XY_bins_hist_var   
0                  0                      0               0.0  \
1                  0                      0               0.0   
2                  0                      0               0.0   
3                  0                      0               0.0   
4                  0                      0               0.0   

   XY_wedges_hist_mean  XY_wedges_hist_median  XY_wedges_hist_mode   
0             4.113306                    4.0                    2  \
1             4.241972                    4.0                    4   
2             4.102663                    4.0                    2   
3             4.723479                    4.0                    3   
4             4.753186                    5.0                    3   

   XY_wedges_hist_min  XY_wedges_hist_max  XY_wedges_hist_range   
0                   1                   8                     7  \
1                   1                   8                     7   
2                   1                   8                     7   
3                   1                   8                     7   
4                   1                   8                     7   

   XY_wedges_hist_stdev  XY_wedges_hist_skew  XY_wedges_hist_kurtosis   
0              2.389146             0.106134                -1.515544  \
1              2.204535             0.135910                -1.154647   
2              2.371178             0.158717                -1.321538   
3              2.191907             0.094337                -1.155488   
4              2.145774            -0.044867                -1.092984   

   XY_wedges_hist_var  Z_slices_hist_mean  Z_slices_hist_median   
0            5.708020            3.477096                   3.0  \
1            4.859973            4.700692                   5.0   
2            5.622487            4.514549                   5.0   
3            4.804458            4.149886                   4.0   
4            4.604348            4.905261                   5.0   

   Z_slices_hist_mode  Z_slices_hist_min  Z_slices_hist_max   
0                 3.0                1.0                6.0  \
1                 6.0                1.0                9.0   
2                 5.0                1.0                8.0   
3                 5.0                0.0                8.0   
4                 6.0                1.0                9.0   

   Z_slices_hist_range  Z_slices_hist_stdev  Z_slices_hist_skew   
0                  5.0             1.468692           -0.118197  \
1                  8.0             2.187697            0.020570   
2                  7.0             1.815533           -0.064242   
3                  

In [64]:
# final_dist_sumstats = pd.concat([hist_df_combo.set_index(["dataset", "image_name", "object"]), hist_center_df_combo.set_index(["dataset", "image_name", "object"])], axis=1, sort=True, )
final_dist_sumstats = pd.concat([hist_df_combo, hist_center_df_combo], axis=0).set_index(["dataset", "image_name", "object"]).sort_index()

final_dist_sumstats.head(22)

XY_bins_hist_mean   
dataset        image_name                            object                           
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER                    3.110104  \
                                                     ERXLD                 3.667051   
                                                     LD                    3.583447   
                                                     golgi                 2.693031   
                                                     golgiXER              2.681647   
                                                     golgiXLD              2.121053   
                                                     golgiXperox           2.079365   
                                                     lyso                  3.260502   
                                                     lysoXER               3.253463   
                                                     lysoXLD               3.494737   
                                                     lysoXgolgi            3.183126   
                                                     lysoXmito             3.350857   
                                                     lysoXperox            3.329114   
                                                     mito                  3.159258   
                                                     mitoXER               3.107463   
                                                     mitoXLD               2.828829   
                                                     mitoXgolgi            2.742611   
                                                     mitoXperox            2.924976   
                                                     nuc                   1.000000   
                                                     perox                 3.151505   
                                                     peroxXER              3.228485   
                                                     peroxXLD              4.000000   

                                                                  XY_bins_hist_median   
dataset        image_name                            object                             
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER                           3.0  \
                                                     ERXLD                        4.0   
                                                     LD                           4.0   
                                                     golgi                        2.0   
                                                     golgiXER                     2.0   
                                                     golgiXLD                     2.0   
                                                     golgiXperox                  2.0   
                                                     lyso                         3.0   
                                                     lysoXER                      3.0   
                                                     lysoXLD                      3.0   
                                                     lysoXgolgi                   3.0   
                                                     lysoXmito                    3.0   
                                                     lysoXperox                   3.0   
                                                     mito                         3.0   
                                                     mitoXER                      3.0   
                                                     mitoXLD                      3.0   
                                                     mitoXgolgi                   3.0   
                                                     mitoXperox                   3.0   
                                                     nuc                          1.0   
                                                     perox                        3.0   
                   

____________________
## 5. Normalize values

#### Volume fraction: organelles, contact sites, nucleus

In [65]:
new_regions_df = regions_df[group_by + ["volume", "surface_area"] +  ['SA_to_volume_ratio', 'equivalent_diameter', 'extent', 
                                                                      'euler_number', 'solidity', 'axis_major_length']].set_index(group_by)
new_regions_df.head(4)

volume   
dataset        image_name                            object                
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc      649.428733  \
                                                     cell    3438.723353   
                                                     cyto    2980.526777   
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc     1218.259749   

                                                             surface_area   
dataset        image_name                            object                 
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc       709.825046  \
                                                     cell     3413.566432   
                                                     cyto     4015.693457   
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc       897.527294   

                                                             SA_to_volume_ratio   
dataset        image_name                            object                       
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc               1.092999  \
                                                     cell              0.992684   
                                                     cyto              1.347310   
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc               0.736729   

                                                             equivalent_diameter   
dataset        image_name                            object                        
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc               10.744288  \
                                                     cell              18.726914   
                                                     cyto              17.855203   
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc               13.250952   

                                                               extent   
dataset        image_name                            object             
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc     0.509973  \
                                                     cell    0.279502   
                                                     cyto    0.242259   
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc     0.606823   

                                                             euler_number   
dataset        image_name                            object                 
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc                1  \
                                                     cell               5   
                                                     cyto               6   
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc                1   

                                                             solidity   
dataset        image_name                            object             
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc     0.848400  \
                                                     cell    0.621498   
                                                     cyto    0.538686   
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc     0.927997   

                                                             axis_major_length  
dataset        image_name                            object                     
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing nuc             19.892745  
                                                     cell            54.612568  
                                                     cyto            57.244780  
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing nuc             23.137948

In [66]:
# organelle volume fraction
org_tot_vol = org_merge_2.loc[org_merge_2.index.unique()[0]][('volume', 'sum')]
cell_tot_vol = new_regions_df.loc[org_merge_2.index.unique()[0][:-1] + ('cell',)]["volume"]
org_vol_fract = org_tot_vol / cell_tot_vol

org_tot_vol, cell_tot_vol, org_vol_fract

(879.5298999916363, 3438.7233528345632, 0.2557722182758999)

In [112]:
area_fractions = []
for idx in org_merge_2.index.unique():
     org_vol = org_merge_2.loc[idx][('volume', 'sum')]
     cell_vol = new_regions_df.loc[idx[:-1] + ('cell',)]["volume"]
     afrac = org_vol/cell_vol
     area_fractions.append(afrac)

org_merge_3[('volume','fraction')] = area_fractions
org_merge_3#.sort_index(axis=1)

volume   
                                                             count   
dataset        image_name                            object          
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER          1  \
                                                     LD         44   
                                                     golgi       5   
                                                     lyso       74   
                                                     mito        4   
...                                                            ...   
               a48hrs-Ctrl_9_Unmixing                LD          1   
                                                     golgi       3   
                                                     lyso      307   
                                                     mito        4   
                                                     perox      96   

                                                                          
                                                                    sum   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD       27.852235   
                                                     golgi    47.892440   
                                                     lyso     90.365857   
                                                     mito    307.653011   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    31.769421   
                                                     lyso    104.637025   
                                                     mito    301.789643   
                                                     perox     8.827322   

                                                                          
                                                                   mean   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.633005   
                                                     golgi     9.578488   
                                                     lyso      1.221160   
                                                     mito     76.913253   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    10.589807   
                                                     lyso      0.340837   
                                                     mito     75.447411   
                                                     perox     0.091951   

                                                                          
                                                                 median   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.171284   
                                                     golgi     2.206830   
                                                     lyso      0.148942   
                                                     mito      3.888639   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi     7.534005   
                                                     lyso      0.071989   
                                                     mito      6.534849   
  

In [68]:
# TODO: try to reorder columns like this
# cols = ['IWWGCW', 'IWWGDW', 'BASE']
# new_cols = df.columns.reindex(cols, level=0)
# df.reindex(columns=new_cols[0]) #new_cols is a single item tuple
# or
# df.reindex(columns=df.columns.reindex(['IWWGCW', 'IWWGDW', 'BASE'], level=0)[0])



In [113]:
# nucleus volume fraction - to be added once everything is unstacked (per cell)
nuc_tot_vol = new_regions_df.loc[org_merge_2.index.unique()[0][:-1] + ('nuc',)]["volume"]
cell_tot_vol = new_regions_df.loc[org_merge_2.index.unique()[0][:-1] + ('cell',)]["volume"]
nuc_area_fract = nuc_tot_vol / cell_tot_vol

nuc_tot_vol, cell_tot_vol, nuc_area_fract

(649.4287327939147, 3438.7233528345632, 0.18885751081388566)

#### Portion of organelle involved in contact site per cell

In [114]:
# contact site total volume (for each type) / org A (or B) total volume
norm_toA_list = []
norm_toB_list = []
for col in contact_merged_2.index:
    org_A = col[-1].split('X')[0]
    org_B = col[-1].split('X')[1]

    contact_v = contact_merged_2.loc[col][('volume', 'sum')]
    org_A_vol = org_merge_3.loc[col[:-1]+(org_A,)][('volume', 'sum')]
    org_B_vol = org_merge_3.loc[col[:-1]+(org_B,)][('volume', 'sum')]

    norm_toA_list.append((contact_v/org_A_vol))
    norm_toB_list.append(contact_v/org_B_vol)

contact_merged_2[('volume', 'norm_to_A')] = norm_toA_list
contact_merged_2[('volume', 'norm_to_B')] = norm_toB_list
contact_merged_2

volume   
                                                                  count   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD           49  \
                                                     golgiXER        33   
                                                     golgiXLD         4   
                                                     golgiXperox      3   
                                                     lysoXER        130   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox      11   
                                                     mitoXER        170   
                                                     mitoXgolgi      30   
                                                     mitoXperox      32   
                                                     peroxXER        93   

                                                                              
                                                                        sum   
dataset        image_name                            object                   
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD         9.418127  \
                                                     golgiXER     17.959975   
                                                     golgiXLD      0.181213   
                                                     golgiXperox   0.059577   
                                                     lysoXER      31.464089   
...                                                                     ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox    0.193625   
                                                     mitoXER      89.596322   
                                                     mitoXgolgi    4.825735   
                                                     mitoXperox    0.739747   
                                                     peroxXER      4.498062   

                                                                             
                                                                      mean   
dataset        image_name                            object                  
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD        0.192207  \
                                                     golgiXER     0.544242   
                                                     golgiXLD     0.045303   
                                                     golgiXperox  0.019859   
                                                     lysoXER      0.242031   
...                                                                    ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox   0.017602   
                                                     mitoXER      0.527037   
                                                     mitoXgolgi   0.160858   
                                                     mitoXperox   0.023117   
                                                     peroxXER     0.048366   

                                                                             
                                                                    median   
dataset        image_name                            object                  
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ERXLD        0.042200  \
                                                     golgiXER     0.024824   
                                                     golgiXLD     0.014894   
                                                     golgiXperox  0.009929   
                                                     lysoXER      0.037236   
...                                                                    ...   
               a48hrs-Ctrl_9_Unmixing                lysoXperox   0.012412   
                                  

#### Portion of individual organelles involved in contacts

In [115]:
# count of organelles in each contact type
collist = [col for col in combo_test.columns if col.endswith(("_count"))]
collist_new = [col.split('_')[0] for col in combo_test.columns if col.endswith(("_count"))]

cont_count_df = combo_test[group_by]
cont_count_df[collist_new] = combo_test[collist].astype(bool)
cont_countperorg = cont_count_df.groupby(group_by).agg('sum')
cont_countperorg.columns = pd.MultiIndex.from_product([cont_countperorg.columns, ['count_in']])
cont_countperorg

for col in cont_countperorg.columns:
    cont_countperorg[(col[0], 'num_fraction_in')] = cont_countperorg[col].values/org_merge_3[('volume', 'count')].values
cont_countperorg.sort_index(axis=1, inplace=True)

cont_countperorg.head()

C:\Users\Shannon\AppData\Local\Temp\ipykernel_26164\3367629639.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cont_count_df[collist_new] = combo_test[collist].astype(bool)
C:\Users\Shannon\AppData\Local\Temp\ipykernel_26164\3367629639.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cont_count_df[collist_new] = combo_test[collist].astype(bool)
C:\Users\Shannon\AppData\Local\Temp\ipykernel_26164\3367629639.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFram

ERXLD   
                                                            count_in   
dataset        image_name                            object            
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER            1  \
                                                     LD           31   
                                                     golgi         0   
                                                     lyso          0   
                                                     mito          0   

                                                                              
                                                            num_fraction_in   
dataset        image_name                            object                   
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER            1.000000  \
                                                     LD            0.704545   
                                                     golgi         0.000000   
                                                     lyso          0.000000   
                                                     mito          0.000000   

                                                            golgiXER   
                                                            count_in   
dataset        image_name                            object            
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER            1  \
                                                     LD            0   
                                                     golgi         5   
                                                     lyso          0   
                                                     mito          0   

                                                                              
                                                            num_fraction_in   
dataset        image_name                            object                   
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER                 1.0  \
                                                     LD                 0.0   
                                                     golgi              1.0   
                                                     lyso               0.0   
                                                     mito               0.0   

                                                            golgiXLD   
                                                            count_in   
dataset        image_name                            object            
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER            0  \
                                                     LD            3   
                                                     golgi         2   
                                                     lyso          0   
                                                     mito          0   

                                                                              
                                                            num_fraction_in   
dataset        image_name                            object                   
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER            0.000000  \
                                                     LD            0.068182   
                                                     golgi         0.400000   
                                                     lyso          0.000000   
                                                     mito          0.000000   

                                                            golgiXperox   
                                                               count_in   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER               0  \
                                                     LD               0   
                                                     golgi

In [116]:
org_merge_4 = pd.merge(org_merge_3, cont_countperorg, on=group_by, how='outer')
org_merge_4

volume   
                                                             count   
dataset        image_name                            object          
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER          1  \
                                                     LD         44   
                                                     golgi       5   
                                                     lyso       74   
                                                     mito        4   
...                                                            ...   
               a48hrs-Ctrl_9_Unmixing                LD          1   
                                                     golgi       3   
                                                     lyso      307   
                                                     mito        4   
                                                     perox      96   

                                                                          
                                                                    sum   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD       27.852235   
                                                     golgi    47.892440   
                                                     lyso     90.365857   
                                                     mito    307.653011   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    31.769421   
                                                     lyso    104.637025   
                                                     mito    301.789643   
                                                     perox     8.827322   

                                                                          
                                                                   mean   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.633005   
                                                     golgi     9.578488   
                                                     lyso      1.221160   
                                                     mito     76.913253   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi    10.589807   
                                                     lyso      0.340837   
                                                     mito     75.447411   
                                                     perox     0.091951   

                                                                          
                                                                 median   
dataset        image_name                            object               
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing ER      879.529900  \
                                                     LD        0.171284   
                                                     golgi     2.206830   
                                                     lyso      0.148942   
                                                     mito      3.888639   
...                                                                 ...   
               a48hrs-Ctrl_9_Unmixing                LD        0.198590   
                                                     golgi     7.534005   
                                                     lyso      0.071989   
                                                     mito      6.534849   
  

__________
## 5. Combine datatables

#### Unstack and flatten dataframes

In [129]:
# unstack and fix column names
new_org_df = org_merge_4.unstack(-1)
for col in new_org_df.columns:
    if col[1] in ('count_in', 'num_fraction_in') or col[0].endswith(('_count', '_volume')):
        if col[2] not in col[0]:
            new_org_df.drop(col,axis=1, inplace=True)

new_col_order = ['dataset', 'image_name', 'object', 'volume', 'surface_area', 'SA_to_volume_ratio', 
                 'equivalent_diameter', 'extent', 'euler_number', 'solidity', 'axis_major_length', 
                 'ERXLD', 'ERXLD_count', 'ERXLD_volume', 'golgiXER', 'golgiXER_count', 'golgiXER_volume', 
                 'golgiXLD', 'golgiXLD_count', 'golgiXLD_volume', 'golgiXperox', 'golgiXperox_count', 'golgiXperox_volume', 
                 'lysoXER', 'lysoXER_count', 'lysoXER_volume', 'lysoXLD', 'lysoXLD_count', 'lysoXLD_volume', 
                 'lysoXgolgi', 'lysoXgolgi_count', 'lysoXgolgi_volume', 'lysoXmito', 'lysoXmito_count', 'lysoXmito_volume', 
                 'lysoXperox', 'lysoXperox_count', 'lysoXperox_volume', 'mitoXER', 'mitoXER_count', 'mitoXER_volume', 
                 'mitoXLD', 'mitoXLD_count', 'mitoXLD_volume', 'mitoXgolgi', 'mitoXgolgi_count', 'mitoXgolgi_volume', 
                 'mitoXperox', 'mitoXperox_count', 'mitoXperox_volume', 'peroxXER', 'peroxXER_count', 'peroxXER_volume', 
                 'peroxXLD', 'peroxXLD_count', 'peroxXLD_volume']
new_cols = new_org_df.columns.reindex(new_col_order, level=0)
new_org_df = new_org_df.reindex(columns=new_cols[0])
new_org_df.columns = ["_".join((col_name[-1], col_name[1], col_name[0])) for col_name in new_org_df.columns.to_flat_index()]

#renaming, filling "NaN" with 0 when needed, and removing ER_std columns
for col in new_org_df.columns:
    if '_count_in_' or '_fraction_in_' in col:
        new_org_df[col] = new_org_df[col].fillna(0)
    if col.endswith(("_count_volume","_sum_volume", "_mean_volume", "_median_volume")):
        new_org_df[col] = new_org_df[col].fillna(0)
    if col.endswith("_count_volume"):
        new_org_df.rename(columns={col:col.split("_")[0]+"_count"}, inplace=True)
    if col.startswith("ER_std_"):
        new_org_df.drop(columns=[col], inplace=True)
new_org_df = new_org_df.reset_index()

new_org_df.head()

dataset                               image_name  ER_count   
0  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_2_Unmixing       1.0  \
1  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_3_Unmixing       1.0   
2  20231101_testa  a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing       1.0   
3  20231101_testa   a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing       1.0   
4  20231101_testa                  a24hrs-Ctrl_10_Unmixing       1.0   

   LD_count  golgi_count  lyso_count  mito_count  perox_count  ER_sum_volume   
0      44.0          5.0        74.0         4.0        125.0     879.529900  \
1      27.0         12.0        65.0         2.0        102.0     685.549756   
2       6.0          5.0       342.0         6.0        102.0     820.856510   
3      24.0         18.0       142.0        11.0        118.0    1805.477710   
4       1.0          4.0        54.0         6.0         83.0     413.834072   

   LD_sum_volume  golgi_sum_volume  lyso_sum_volume  mito_sum_volume   
0      27.852235         47.892440        90.365857       307.653011  \
1      10.001484         39.387827        45.338077       275.024688   
2       2.105053         32.494274       103.219590       243.647482   
3      23.180408         84.544691       146.760428       467.006521   
4       1.104656         43.471332        41.897507       237.456441   

   perox_sum_volume  ER_mean_volume  LD_mean_volume  golgi_mean_volume   
0         13.196300      879.529900        0.633005           9.578488  \
1          7.615923      685.549756        0.370425           3.282319   
2         11.582757      820.856510        0.350842           6.498855   
3         14.037824     1805.477710        0.965850           4.696927   
4          4.875382      413.834072        1.104656          10.867833   

   lyso_mean_volume  mito_mean_volume  perox_mean_volume  ER_median_volume   
0          1.221160         76.913253           0.105570        879.529900  \
1          0.697509        137.512344           0.074666        685.549756   
2          0.301812         40.607914           0.113556        820.856510   
3          1.033524         42.455138           0.118965       1805.477710   
4          0.775880         39.576074           0.058740        413.834072   

   LD_median_volume  golgi_median_volume  lyso_median_volume   
0          0.171284             2.206830            0.148942  \
1          0.153907             1.764968            0.161354   
2          0.079436             2.507198            0.064542   
3          0.137772             1.689255            0.140254   
4          1.104656             0.772018            0.413315   

   mito_median_volume  perox_median_volume  LD_std_volume  golgi_std_volume   
0            3.888639             0.079436       2.622293         12.753749  \
1          137.512344             0.055853       0.506124          5.485685   
2            5.144720             0.084401       0.554328          6.343030   
3            6.943200             0.095571       1.977027          7.323348   
4            5.688360             0.049647       0.000000         20.505605   

   lyso_std_volume  mito_std_volume  perox_std_volume  ER_fraction_volume   
0         4.959244       148.450572          0.093335            0.255772  \
1         1.873366       186.674764          0.068917            0.181145   
2         2.032176        88.905238          0.097076            0.252775   
3         3.133922        99.478058          0.106663            0.293628   
4         1.120100        80.191045          0.043242            0.124551   

   LD_fraction_volume  golgi_fraction_volume  lyso_fraction_volume   
0            0.008100               0.013927              0.026279  \
1            0.002643               0.010408              0.011980   
2            0.000648               0.010006              0.031786   
3            0.003770               0.013750              0.023868   
4            0.000332               0.013083              0.012610   

   mi

In [132]:
new_contact_df = contact_merged_2.unstack(-1)
new_contact_df.columns.levels[0]

Index(['SA_to_volume_ratio', 'axis_major_length', 'equivalent_diameter',
       'euler_number', 'extent', 'solidity', 'surface_area', 'volume'],
      dtype='object')

In [133]:
# unstack and fix column names
new_contact_df = contact_merged_2.unstack(-1)
new_contact_df.columns = ["_".join((col_name[-1], col_name[1], col_name[0])) for col_name in new_contact_df.columns.to_flat_index()]

#renaming and filling "NaN" with 0 when needed
for col in new_contact_df.columns:
    if col.endswith(("_count_volume","_sum_volume", "_mean_volume", "_median_volume")):
        new_contact_df[col] = new_contact_df[col].fillna(0)
    if col.endswith("_count_volume"):
        new_contact_df.rename(columns={col:col.split("_")[0]+"_count"}, inplace=True)

new_contact_df = new_contact_df.reset_index()

new_contact_df.head()

dataset                               image_name  ERXLD_count   
0  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_2_Unmixing         49.0  \
1  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_3_Unmixing         29.0   
2  20231101_testa  a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing          6.0   
3  20231101_testa   a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing         34.0   
4  20231101_testa                  a24hrs-Ctrl_10_Unmixing          1.0   

   golgiXER_count  golgiXLD_count  golgiXperox_count  lysoXER_count   
0            33.0             4.0                3.0          130.0  \
1            54.0             1.0                2.0          136.0   
2            39.0             0.0                1.0          253.0   
3            71.0             2.0                4.0          279.0   
4            39.0             0.0                2.0          104.0   

   lysoXLD_count  lysoXgolgi_count  lysoXmito_count  lysoXperox_count   
0            3.0              15.0             86.0               9.0  \
1            1.0              24.0             77.0               3.0   
2            0.0              25.0             90.0              13.0   
3            3.0              49.0            151.0              12.0   
4            1.0               6.0             82.0               2.0   

   mitoXER_count  mitoXLD_count  mitoXgolgi_count  mitoXperox_count   
0          129.0           15.0              30.0              56.0  \
1          303.0            8.0              48.0              24.0   
2          172.0            3.0              21.0              49.0   
3          178.0           12.0              65.0              33.0   
4          278.0            0.0              22.0              20.0   

   peroxXER_count  peroxXLD_count  ERXLD_sum_volume  golgiXER_sum_volume   
0           123.0             4.0          9.418127            17.959975  \
1            88.0             1.0          1.573825            11.111106   
2           106.0             0.0          0.464204            10.301852   
3           124.0             2.0          7.124413            35.912503   
4            71.0             0.0          1.079833            10.927410   

   golgiXLD_sum_volume  golgiXperox_sum_volume  lysoXER_sum_volume   
0             0.181213                0.059577           31.464089  \
1             0.032271                0.022341           10.408594   
2             0.000000                0.014894           29.445919   
3             0.052130                0.059577           45.040192   
4             0.000000                0.057095            9.117759   

   lysoXLD_sum_volume  lysoXgolgi_sum_volume  lysoXmito_sum_volume   
0            0.161354               1.593684             14.003071  \
1            0.029788               0.886207              6.037133   
2            0.000000               0.940820             13.312971   
3            0.057095               6.369771             16.088265   
4            0.978055               1.030185              5.654848   

   lysoXperox_sum_volume  mitoXER_sum_volume  mitoXLD_sum_volume   
0               0.253202          146.772840            0.148942  \
1               0.022341           75.228341            0.173766   
2               0.126601           84.902152            0.042200   
3               0.238308          226.020144            0.268096   
4               0.007447           50.161330            0.000000   

   mitoXgolgi_sum_volume  mitoXperox_sum_volume  peroxXER_sum_volume   
0              13.010122               1.449706             9.112795  \
1               5.662295               0.444345             2.919272   
2               8.489719               1.114586             7.645712   
3              21.080319               1.144374             6.501337   
4               6.575808               0.310297             2.325984   

   peroxXLD_sum_volume  ERXLD_mean_volume  golgiXER_mean_volume   
0             0.173766           0.192207              0.5

In [141]:
# unstack and fix column names
new_dist_df = final_dist_sumstats.unstack(-1)
new_dist_df.columns = ["_".join((col_name[1], col_name[0])) for col_name in new_dist_df.columns.to_flat_index()]

new_dist_df = new_dist_df.reset_index()

new_dist_df.head()

dataset                               image_name   
0  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_2_Unmixing  \
1  20231101_testa    24hrs-Ctrl +oleicAcid 50uM_3_Unmixing   
2  20231101_testa  a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing   
3  20231101_testa   a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing   
4  20231101_testa                  a24hrs-Ctrl_10_Unmixing   

   ER_XY_bins_hist_mean  ERXLD_XY_bins_hist_mean  LD_XY_bins_hist_mean   
0              3.110104                 3.667051              3.583447  \
1              2.947835                 2.455988              2.629512   
2              3.073872                 4.264505              3.990512   
3              3.011812                 3.115100              2.911738   
4              3.010759                 4.000000              4.000000   

   golgi_XY_bins_hist_mean  golgiXER_XY_bins_hist_mean   
0                 2.693031                    2.681647  \
1                 2.606267                    2.569227   
2                 2.410224                    2.503400   
3                 2.324240                    2.326598   
4                 2.879930                    2.868911   

   golgiXLD_XY_bins_hist_mean  golgiXperox_XY_bins_hist_mean   
0                    2.121053                       2.079365  \
1                    2.000000                       2.500000   
2                         NaN                       3.000000   
3                    2.000000                       3.000000   
4                         NaN                       2.430556   

   lyso_XY_bins_hist_mean  lysoXER_XY_bins_hist_mean   
0                3.260502                   3.253463  \
1                3.033799                   2.901112   
2                2.095889                   2.103797   
3                2.549204                   2.606046   
4                3.115232                   3.047811   

   lysoXLD_XY_bins_hist_mean  lysoXgolgi_XY_bins_hist_mean   
0                   3.494737                      3.183126  \
1                   4.000000                      3.060939   
2                        NaN                      2.434248   
3                   2.137931                      2.288382   
4                   4.000000                      2.993519   

   lysoXmito_XY_bins_hist_mean  lysoXperox_XY_bins_hist_mean   
0                     3.350857                      3.329114  \
1                     3.058168                      2.607143   
2                     2.243737                      1.970874   
3                     2.446806                      2.554348   
4                     3.326647                      3.666667   

   mito_XY_bins_hist_mean  mitoXER_XY_bins_hist_mean   
0                3.159258                   3.107463  \
1                2.889516                   2.860229   
2                2.879770                   2.859697   
3                2.791131                   2.788456   
4                3.263945                   3.163836   

   mitoXLD_XY_bins_hist_mean  mitoXgolgi_XY_bins_hist_mean   
0                   2.828829                      2.742611  \
1                   3.039409                      2.584635   
2                   4.200000                      2.432524   
3                   2.375479                      2.376124   
4                        NaN                      2.893846   

   mitoXperox_XY_bins_hist_mean  nuc_XY_bins_hist_mean   
0                      2.924976                    1.0  \
1                      2.497427                    1.0   
2                      3.275651                    1.0   
3                      3.330347                    1.0   
4                      3.697842                    1.0   

   perox_XY_bins_hist_mean  peroxXER_XY_bins_hist_mean   
0                 3.151505                    3.228485  \
1                 3.152884                    3.133931   
2                 3.095137                    3.041638   
3                 3.513776                    3.526282   
4             

In [142]:
# unstack and fix column names
new_regions_df = regions_df[group_by + ["volume", "surface_area"] +  ['SA_to_volume_ratio', 'equivalent_diameter', 'extent', 
                                                                      'euler_number', 'solidity', 'axis_major_length']].set_index(group_by)
new_regions_df = new_regions_df.unstack(-1)
new_regions_df.columns = ["_".join((col_name[1], col_name[0])) for col_name in new_regions_df.columns.to_flat_index()]
new_regions_df['nuc_area_fraction'] = new_regions_df['nuc_volume'] / new_regions_df['cell_volume']
new_regions_df = new_regions_df.reset_index()

new_regions_df

dataset                               image_name  cell_volume   
0   20231101_testa    24hrs-Ctrl +oleicAcid 50uM_2_Unmixing  3438.723353  \
1   20231101_testa    24hrs-Ctrl +oleicAcid 50uM_3_Unmixing  3784.542862   
2   20231101_testa  a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing  3247.374525   
3   20231101_testa   a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing  6148.852587   
4   20231101_testa                  a24hrs-Ctrl_10_Unmixing  3322.620243   
5   20231101_testa                  a24hrs-Ctrl_14_Unmixing  3835.846084   
6   20231101_testa     a48hrs-Ctrl + oleic acid_01_Unmixing  2302.843664   
7   20231101_testa     a48hrs-Ctrl + oleic acid_02_Unmixing  3564.274378   
8   20231101_testa     a48hrs-Ctrl + oleic acid_07_Unmixing  3460.163616   
9   20231101_testa                  a48hrs-Ctrl_10_Unmixing  3203.106351   
10  20231101_testa                   a48hrs-Ctrl_7_Unmixing  1778.360257   
11  20231101_testa                   a48hrs-Ctrl_8_Unmixing  2507.339144   
12  20231101_testa                   a48hrs-Ctrl_9_Unmixing  2740.540796   

    cyto_volume   nuc_volume  cell_surface_area  cyto_surface_area   
0   2980.526777   649.428733        3413.566432        4015.693457  \
1   2799.685837  1218.259749        3689.379436        4479.403964   
2   2371.565703  1047.025597        2687.745137        3334.611548   
3   5054.937429  1321.017617        4841.224010        5704.205723   
4   2534.245595   981.404043        2848.798996        3500.173258   
5   2946.076391  1037.508176        2608.725791        3214.224462   
6   2015.811733   464.759973        2435.898850        2993.902688   
7   2987.760414   722.539609        2710.595740        3249.221834   
8   1965.814241  1713.890524        2319.760996        3317.467508   
9   1813.704297  1637.721363        2209.314201        3195.901763   
10   723.207368  1255.952115        1643.936608        2397.922761   
11  1979.333249   679.388504        2825.952307        3348.269771   
12  2063.689279   801.146461        2143.461976        2640.032217   

    nuc_surface_area  cell_SA_to_volume_ratio  cyto_SA_to_volume_ratio   
0         709.825046                 0.992684                 1.347310  \
1         897.527294                 0.974855                 1.599967   
2         740.357914                 0.827667                 1.406080   
3         974.698978                 0.787338                 1.128442   
4         750.369991                 0.857395                 1.381150   
5         650.256734                 0.680091                 1.091019   
6         684.917229                 1.057779                 1.485209   
7         625.995482                 0.760490                 1.087511   
8        1065.173921                 0.670419                 1.687579   
9        1106.597172                 0.689741                 1.762085   
10        848.093595                 0.924411                 3.315678   
11        613.308149                 1.127072                 1.691615   
12        562.587779                 0.782131                 1.279278   

    nuc_SA_to_volume_ratio  cell_equivalent_diameter   
0                 1.092999                 18.726914  \
1                 0.736729                 19.334737   
2                 0.707106                 18.372909   
3                 0.737840                 22.729950   
4                 0.764588                 18.513734   
5                 0.626749                 19.421712   
6                 1.473701                 16.384076   
7                 0.866382                 18.952107   
8                 0.621495                 18.765753   
9                 0.675693                 18.289040   
10                0.675259                 15.031663   
11                0.902736                 16.855365   
12                0.702228                 17.362512   

    cyto_equivalent_diameter  nuc_equivalent_diameter  cell_extent   
0                  17.855203                10.744288     0.279502  \
1  

#### Combine unstacked and flattened dataframes

In [143]:
combined_tab1 = pd.merge(new_org_df, new_contact_df, on=["dataset", "image_name"], how="outer")
combined_tab2 = pd.merge(combined_tab1, new_dist_df, on=["dataset", "image_name"], how="outer")
combined_tab3 = pd.merge(combined_tab2, new_regions_df, on=["dataset", "image_name"], how="outer").set_index(["dataset", "image_name"])

In [144]:
combined_tab3.reset_index()

dataset                               image_name  ER_count   
0   20231101_testa    24hrs-Ctrl +oleicAcid 50uM_2_Unmixing       1.0  \
1   20231101_testa    24hrs-Ctrl +oleicAcid 50uM_3_Unmixing       1.0   
2   20231101_testa  a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing       1.0   
3   20231101_testa   a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing       1.0   
4   20231101_testa                  a24hrs-Ctrl_10_Unmixing       1.0   
5   20231101_testa                  a24hrs-Ctrl_14_Unmixing       1.0   
6   20231101_testa     a48hrs-Ctrl + oleic acid_01_Unmixing       1.0   
7   20231101_testa     a48hrs-Ctrl + oleic acid_02_Unmixing       1.0   
8   20231101_testa     a48hrs-Ctrl + oleic acid_07_Unmixing       1.0   
9   20231101_testa                  a48hrs-Ctrl_10_Unmixing       1.0   
10  20231101_testa                   a48hrs-Ctrl_7_Unmixing       1.0   
11  20231101_testa                   a48hrs-Ctrl_8_Unmixing       1.0   
12  20231101_testa                   a48hrs-Ctrl_9_Unmixing       1.0   

    LD_count  golgi_count  lyso_count  mito_count  perox_count  ER_sum_volume   
0       44.0          5.0        74.0         4.0        125.0     879.529900  \
1       27.0         12.0        65.0         2.0        102.0     685.549756   
2        6.0          5.0       342.0         6.0        102.0     820.856510   
3       24.0         18.0       142.0        11.0        118.0    1805.477710   
4        1.0          4.0        54.0         6.0         83.0     413.834072   
5        1.0         10.0       101.0         7.0         27.0     229.631999   
6       17.0          1.0        67.0         3.0         93.0     343.371889   
7       15.0          2.0       116.0         4.0        147.0     824.661989   
8        5.0          4.0        92.0         4.0        129.0    1112.170536   
9       15.0          2.0       127.0         2.0        121.0     404.825537   
10       0.0          3.0       427.0         5.0          3.0       5.488529   
11       0.0          5.0        22.0         5.0        111.0     521.117308   
12       1.0          3.0       307.0         4.0         96.0     632.124104   

    LD_sum_volume  golgi_sum_volume  lyso_sum_volume  mito_sum_volume   
0       27.852235         47.892440        90.365857       307.653011  \
1       10.001484         39.387827        45.338077       275.024688   
2        2.105053         32.494274       103.219590       243.647482   
3       23.180408         84.544691       146.760428       467.006521   
4        1.104656         43.471332        41.897507       237.456441   
5        4.565086         50.935830        72.170057       256.007221   
6       20.370360         25.238296        29.507979       259.907031   
7       19.940910         42.808538       153.048281       336.925164   
8        0.920961         65.907027       170.352910       483.454731   
9        3.256875         38.054792       128.971736       214.479588   
10       0.000000         58.402811       104.825685       144.906095   
11       0.000000         49.952810        45.137005       284.162306   
12       0.198590         31.769421       104.637025       301.789643   

    perox_sum_volume  ER_mean_volume  LD_mean_volume  golgi_mean_volume   
0          13.196300      879.529900        0.633005           9.578488  \
1           7.615923      685.549756        0.370425           3.282319   
2          11.582757      820.856510        0.350842           6.498855   
3          14.037824     1805.477710        0.965850           4.696927   
4           4.875382      413.834072        1.104656          10.867833   
5           0.836560      229.631999        4.565086           5.093583   
6           8.740439      343.371889        1.198256          25.238296   
7          15.028292      824.661989        1.329394          21.404269   
8          10.396182     1112.170536        0.184192          16.476757   
9          17.297181      404.825537        0.217125          19.027396   
10   

In [152]:
combined_tab3.columns = [col.replace('sum', 'total') for col in combined_tab3.columns]
combined_tab3

ER_count  LD_count   
dataset        image_name                                                    
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing         1.0      44.0  \
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing         1.0      27.0   
               a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing       1.0       6.0   
               a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing        1.0      24.0   
               a24hrs-Ctrl_10_Unmixing                       1.0       1.0   
               a24hrs-Ctrl_14_Unmixing                       1.0       1.0   
               a48hrs-Ctrl + oleic acid_01_Unmixing          1.0      17.0   
               a48hrs-Ctrl + oleic acid_02_Unmixing          1.0      15.0   
               a48hrs-Ctrl + oleic acid_07_Unmixing          1.0       5.0   
               a48hrs-Ctrl_10_Unmixing                       1.0      15.0   
               a48hrs-Ctrl_7_Unmixing                        1.0       0.0   
               a48hrs-Ctrl_8_Unmixing                        1.0       0.0   
               a48hrs-Ctrl_9_Unmixing                        1.0       1.0   

                                                        golgi_count   
dataset        image_name                                             
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing            5.0  \
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing           12.0   
               a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing          5.0   
               a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing          18.0   
               a24hrs-Ctrl_10_Unmixing                          4.0   
               a24hrs-Ctrl_14_Unmixing                         10.0   
               a48hrs-Ctrl + oleic acid_01_Unmixing             1.0   
               a48hrs-Ctrl + oleic acid_02_Unmixing             2.0   
               a48hrs-Ctrl + oleic acid_07_Unmixing             4.0   
               a48hrs-Ctrl_10_Unmixing                          2.0   
               a48hrs-Ctrl_7_Unmixing                           3.0   
               a48hrs-Ctrl_8_Unmixing                           5.0   
               a48hrs-Ctrl_9_Unmixing                           3.0   

                                                        lyso_count   
dataset        image_name                                            
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing          74.0  \
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing          65.0   
               a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing       342.0   
               a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing        142.0   
               a24hrs-Ctrl_10_Unmixing                        54.0   
               a24hrs-Ctrl_14_Unmixing                       101.0   
               a48hrs-Ctrl + oleic acid_01_Unmixing           67.0   
               a48hrs-Ctrl + oleic acid_02_Unmixing          116.0   
               a48hrs-Ctrl + oleic acid_07_Unmixing           92.0   
               a48hrs-Ctrl_10_Unmixing                       127.0   
               a48hrs-Ctrl_7_Unmixing                        427.0   
               a48hrs-Ctrl_8_Unmixing                         22.0   
               a48hrs-Ctrl_9_Unmixing                        307.0   

                                                        mito_count   
dataset        image_name                                            
20231101_testa 24hrs-Ctrl +oleicAcid 50uM_2_Unmixing           4.0  \
               24hrs-Ctrl +oleicAcid 50uM_3_Unmixing           2.0   
               a24hrs-Ctrl +oleicAcid 50uM_10_Unmixing         6.0   
               a24hrs-Ctrl +oleicAcid 50uM_4_Unmixing         11.0   
               a24hrs-Ctrl_10_Unmixing                         6.0   
               a24hrs-Ctrl_14_Unmixing                         7.0   
               a48hrs-Ctrl + oleic acid_01_Unmixing            3.0   
               a48hrs-Ctrl + oleic acid_02_Unmixing            4.0   
               a48hrs-Ctrl + oleic acid_07_Unmixing            4.0  

__________________
# Newer function from C2-109 analysis

In [153]:
def _batch_summary_stats(csv_path_list: List[str],
                         out_path: str,
                         out_preffix: str):
    """" 
    csv_path_list: List[str],
        A list of path strings where .csv files to analyze are located.
    out_path: str,
        A path string where the summary data file will be output to
    out_preffix: str
        The prefix used to name the output file.    
    """
    ds_count = 0
    fl_count = 0
    ###################
    # Read in the csv files and combine them into one of each type
    ###################
    org_tabs = []
    contact_tabs = []
    dist_tabs = []
    region_tabs = []
    
    org = "_organelles"
    contacts = "_contacts"
    dist = "_distributions"
    regions = "_regions"

    for loc in csv_path_list:
        ds_count = ds_count + 1
        files_store = sorted(loc.glob("*.csv"))
        for file in files_store:
            fl_count = fl_count + 1
            stem = file.stem

            # org = "organelles" TODO: get rid of these (moved to the above)
            # contacts = "contacts"
            # dist = "distributions"
            # regions = "_regions"

            if org in stem:
                test_orgs = pd.read_csv(file, index_col=0)
                test_orgs.insert(0, "dataset", stem[:-11])
                org_tabs.append(test_orgs)
            if contacts in stem:
                test_contact = pd.read_csv(file, index_col=0)
                test_contact.insert(0, "dataset", stem[:-9])
                contact_tabs.append(test_contact)
            if dist in stem:
                test_dist = pd.read_csv(file, index_col=0)
                test_dist.insert(0, "dataset", stem[:-14])
                dist_tabs.append(test_dist)
            if regions in stem:
                test_regions = pd.read_csv(file, index_col=0)
                test_regions.insert(0, "dataset", stem[:-8])
                region_tabs.append(test_regions)
            
    org_df = pd.concat(org_tabs,axis=0, join='outer')
    contacts_df = pd.concat(contact_tabs,axis=0, join='outer')
    dist_df = pd.concat(dist_tabs,axis=0, join='outer')
    regions_df = pd.concat(region_tabs,axis=0, join='outer')

    ###################
    # adding new metrics to the original sheets
    ###################
    # TODO: include these labels when creating the original sheets
    contact_cnt = contacts_df[["dataset", "image_name", "object", "label", "volume"]]
    contact_cnt[["orgA", "orgB"]] = contact_cnt["object"].str.split('X', expand=True)
    contact_cnt[["A_ID", "B_ID"]] = contact_cnt["label"].str.split('_', expand=True)
    contact_cnt["A"] = contact_cnt["orgA"] +"_" + contact_cnt["A_ID"].astype(str)
    contact_cnt["B"] = contact_cnt["orgB"] +"_" + contact_cnt["B_ID"].astype(str)

    contact_cnt_percell = contact_cnt[["dataset", "image_name", "orgA", "A_ID", "object", "volume"]].groupby(["dataset", "image_name", "orgA", "A_ID", "object"]).agg(["count", "sum"])
    contact_cnt_percell.columns = ["_".join(col_name).rstrip('_') for col_name in contact_cnt_percell.columns.to_flat_index()]
    unstacked = contact_cnt_percell.unstack(level='object')
    unstacked.columns = ["_".join(col_name).rstrip('_') for col_name in unstacked.columns.to_flat_index()]
    unstacked = unstacked.reset_index()
    for col in unstacked.columns:
        if col.startswith("volume_count_"):
            newname = col.split("_")[-1] + "_count"
            unstacked.rename(columns={col:newname}, inplace=True)
        if col.startswith("volume_sum_"):
            newname = col.split("_")[-1] + "_volume"
            unstacked.rename(columns={col:newname}, inplace=True)
    unstacked.rename(columns={"orgA":"object", "A_ID":"label"}, inplace=True)
    unstacked.set_index(['dataset', 'image_name', 'object', 'label'])

    contact_percellB = contact_cnt[["dataset", "image_name", "orgB", "B_ID", "object", "volume"]].groupby(["dataset", "image_name", "orgB", "B_ID", "object"]).agg(["count", "sum"])
    contact_percellB.columns = ["_".join(col_name).rstrip('_') for col_name in contact_percellB.columns.to_flat_index()]
    unstackedB = contact_percellB.unstack(level='object')
    unstackedB.columns = ["_".join(col_name).rstrip('_') for col_name in unstackedB.columns.to_flat_index()]
    unstackedB = unstackedB.reset_index()
    for col in unstackedB.columns:
        if col.startswith("volume_count_"):
            newname = col.split("_")[-1] + "_count"
            unstackedB.rename(columns={col:newname}, inplace=True)
        if col.startswith("volume_sum_"):
            newname = col.split("_")[-1] + "_volume"
            unstackedB.rename(columns={col:newname}, inplace=True)
    unstackedB.rename(columns={"orgB":"object", "B_ID":"label"}, inplace=True)
    unstackedB.set_index(['dataset', 'image_name', 'object', 'label'])

    contact_cnt = pd.concat([unstacked, unstackedB], axis=0).sort_index(axis=0)
    contact_cnt = contact_cnt.groupby(['dataset', 'image_name', 'object', 'label']).sum().reset_index()
    contact_cnt['label']=contact_cnt['label'].astype("Int64")

    org_df = pd.merge(org_df, contact_cnt, how='left', on=['dataset', 'image_name', 'object', 'label'], sort=True)
    org_df[contact_cnt.columns] = org_df[contact_cnt.columns].fillna(0)

    ###################
    # summary stat group
    ###################
    group_by = ['dataset', 'image_name', 'object']
    sharedcolumns = ["SA_to_volume_ratio", "equivalent_diameter", "extent", "euler_number", "solidity", "axis_major_length"]
    ag_func_standard = ['mean', 'median', 'std']

    ###################
    # summarize shared measurements between org_df and contacts_df
    ###################
    org_cont_tabs = []
    for tab in [org_df, contacts_df]:
        tab1 = tab[group_by + ['volume']].groupby(group_by).agg(['count', 'sum'] + ag_func_standard)
        tab2 = tab[group_by + ['surface_area']].groupby(group_by).agg(['sum'] + ag_func_standard)
        tab3 = tab[group_by + sharedcolumns].groupby(group_by).agg(ag_func_standard)
        shared_metrics = pd.merge(tab1, tab2, 'outer', on=group_by)
        shared_metrics = pd.merge(shared_metrics, tab3, 'outer', on=group_by)
        org_cont_tabs.append(shared_metrics)

    org_summary = org_cont_tabs[0]
    contact_summary = org_cont_tabs[1]

    ###################
    # group metrics from regions_df similar to the above
    ###################
    regions_summary = regions_df[group_by + ['volume', 'surface_area'] + sharedcolumns].set_index(group_by)

    ###################
    # summarize extra metrics from org_df
    ###################
    columns2 = [col for col in org_df.columns if col.endswith(("_count", "_volume"))]
    contact_counts_summary = org_df[group_by + columns2].groupby(group_by).agg(['sum'] + ag_func_standard)
    org_summary = pd.merge(org_summary, contact_counts_summary, 'outer', on=group_by)#left_on=group_by, right_on=True)

    ###################
    # summarize distribution measurements
    ###################
    # organelle distributions
    hist_dfs = []
    for ind in dist_df.index:
        selection = dist_df.loc[[ind]]
        bins_df = pd.DataFrame()
        wedges_df = pd.DataFrame()
        Z_df = pd.DataFrame()

        bins_df[['bins', 'masks', 'obj']] = selection[['XY_bins', 'XY_mask_vox_cnt_perbin', 'XY_obj_vox_cnt_perbin']]
        wedges_df[['bins', 'masks', 'obj']] = selection[['XY_wedges', 'XY_mask_vox_cnt_perwedge', 'XY_obj_vox_cnt_perwedge']]
        Z_df[['bins', 'masks', 'obj']] = selection[['Z_slices', 'Z_mask_vox_cnt', 'Z_obj_vox_cnt']]

        dfs = [selection[['dataset', 'image_name', 'object']].reset_index()]
        for df, prefix in zip([bins_df, wedges_df, Z_df], ["XY_bins_", "XY_wedges_", "Z_slices_"]):
            single_df = pd.DataFrame(list(zip(df["bins"].values[0][1:-1].split(", "), 
                                            df["obj"].values[0][1:-1].split(", "), 
                                            df["masks"].values[0][1:-1].split(", "))), columns =['bins', 'obj', 'mask']).astype(int)
            
            single_df['mask_fract'] = single_df['mask']/single_df['mask'].max()
            single_df['obj_norm'] = (single_df["obj"]/single_df["mask_fract"]).fillna(0)
            single_df['portion_per_bin'] = (single_df["obj"] / single_df["obj"].sum())*100

            if "Z_" in prefix:
                single_df['bins'] = (single_df["bins"]/max(single_df.bins)*10).apply(np.floor)

            sumstats_df = pd.DataFrame()

            s = single_df['bins'].repeat(single_df['obj_norm'])
            sumstats_df['hist_mean']=[s.mean()]
            sumstats_df['hist_median']=[s.median()]
            if single_df['obj_norm'].sum() != 0: sumstats_df['hist_mode']=[s.mode()[0]]
            else: sumstats_df['hist_mode']=['NaN']
            sumstats_df['hist_min']=[s.min()]
            sumstats_df['hist_max']=[s.max()]
            sumstats_df['hist_range']=[s.max() - s.min()]
            sumstats_df['hist_stdev']=[s.std()]
            sumstats_df['hist_skew']=[s.skew()]
            sumstats_df['hist_kurtosis']=[s.kurtosis()]
            sumstats_df['hist_var']=[s.var()]
            sumstats_df.columns = [prefix+col for col in sumstats_df.columns]
            dfs.append(sumstats_df.reset_index())
        combined_df = pd.concat(dfs, axis=1).drop(columns="index")
        hist_dfs.append(combined_df)
    dist_org_summary = pd.concat(hist_dfs, ignore_index=True)

    # nucleus distribution
    nuc_dist_df = dist_df[["dataset", "image_name", 
                        "XY_bins", "XY_center_vox_cnt_perbin", "XY_mask_vox_cnt_perbin",
                        "XY_wedges", "XY_center_vox_cnt_perwedge", "XY_mask_vox_cnt_perwedge",
                        "Z_slices", "Z_center_vox_cnt", "Z_mask_vox_cnt"]].set_index(["dataset", "image_name"])
    nuc_hist_dfs = []
    for idx in nuc_dist_df.index.unique():
        selection = nuc_dist_df.loc[idx].iloc[[0]].reset_index()
        bins_df = pd.DataFrame()
        wedges_df = pd.DataFrame()
        Z_df = pd.DataFrame()

        bins_df[['bins', 'center', 'masks']] = selection[['XY_bins', 'XY_center_vox_cnt_perbin', 'XY_mask_vox_cnt_perbin']]
        wedges_df[['bins', 'center', 'masks']] = selection[['XY_wedges', 'XY_center_vox_cnt_perwedge', 'XY_mask_vox_cnt_perwedge']]
        Z_df[['bins', 'center', 'masks']] = selection[['Z_slices', 'Z_center_vox_cnt', 'Z_mask_vox_cnt']]

        dfs = [selection[['dataset', 'image_name']]]
        for df, prefix in zip([bins_df, wedges_df, Z_df], ["XY_bins_", "XY_wedges_", "Z_slices_"]):
            single_df = pd.DataFrame(list(zip(df["bins"].values[0][1:-1].split(", "), 
                                            df["masks"].values[0][1:-1].split(", "),
                                            df["center"].values[0][1:-1].split(", "))), columns =['bins', 'mask', 'obj']).astype(int)
            single_df['mask_fract'] = single_df['mask']/single_df['mask'].max()
            single_df['obj_norm'] = (single_df["obj"]/single_df["mask_fract"]).fillna(0)
            single_df['portion_per_bin'] = (single_df["obj"] / single_df["obj"].sum())*100
            if "Z_" in prefix:
                single_df['bins'] = (single_df["bins"]/max(single_df.bins)*10).apply(np.floor)

            sumstats_df = pd.DataFrame()

            s = single_df['bins'].repeat(single_df['obj_norm'])
            sumstats_df['hist_mean']=[s.mean()]
            sumstats_df['hist_median']=[s.median()]
            if single_df['obj_norm'].sum() != 0: sumstats_df['hist_mode']=[s.mode()[0]]
            else: sumstats_df['hist_mode']=['NaN']
            sumstats_df['hist_min']=[s.min()]
            sumstats_df['hist_max']=[s.max()]
            sumstats_df['hist_range']=[s.max() - s.min()]
            sumstats_df['hist_stdev']=[s.std()]
            sumstats_df['hist_skew']=[s.skew()]
            sumstats_df['hist_kurtosis']=[s.kurtosis()]
            sumstats_df['hist_var']=[s.var()]
            sumstats_df.columns = [prefix+col for col in sumstats_df.columns]
            dfs.append(sumstats_df.reset_index())
        combined_df = pd.concat(dfs, axis=1).drop(columns="index")
        nuc_hist_dfs.append(combined_df)
    dist_center_summary = pd.concat(nuc_hist_dfs, ignore_index=True)
    dist_center_summary.insert(2, column="object", value="nuc")

    dist_summary = pd.concat([dist_org_summary, dist_center_summary], axis=0).set_index(group_by).sort_index()

    ###################
    # add normalization
    ###################
    # organelle area fraction
    area_fractions = []
    for idx in org_summary.index.unique():
        org_vol = org_summary.loc[idx][('volume', 'sum')]
        cell_vol = regions_summary.loc[idx[:-1] + ('cell',)]["volume"]
        afrac = org_vol/cell_vol
        area_fractions.append(afrac)
    org_summary[('volume', 'fraction')] = area_fractions
    # TODO: add in line to reorder the level=0 columns here

    # contact sites volume normalized
    norm_toA_list = []
    norm_toB_list = []
    for col in contact_summary.index:
        norm_toA_list.append(contact_summary.loc[col][('volume', 'sum')]/org_summary.loc[col[:-1]+(col[-1].split('X')[0],)][('volume', 'sum')])
        norm_toB_list.append(contact_summary.loc[col][('volume', 'sum')]/org_summary.loc[col[:-1]+(col[-1].split('X')[1],)][('volume', 'sum')])
    contact_summary[('volume', 'norm_to_A')] = norm_toA_list
    contact_summary[('volume', 'norm_to_B')] = norm_toB_list

    # number and area of individuals organelle involved in contact
    cont_cnt = org_df[group_by]
    cont_cnt[[col.split('_')[0] for col in org_df.columns if col.endswith(("_count"))]] = org_df[[col for col in org_df.columns if col.endswith(("_count"))]].astype(bool)
    cont_cnt_perorg = cont_cnt.groupby(group_by).agg('sum')
    cont_cnt_perorg.columns = pd.MultiIndex.from_product([cont_cnt_perorg.columns, ['count_in']])
    for col in cont_cnt_perorg.columns:
        cont_cnt_perorg[(col[0], 'num_fraction_in')] = cont_cnt_perorg[col].values/org_summary[('volume', 'count')].values
    cont_cnt_perorg.sort_index(axis=1, inplace=True)
    org_summary = pd.merge(org_summary, cont_cnt_perorg, on=group_by, how='outer')


    ###################
    # flatten datasheets and combine
    # TODO: restructure this so that all of the datasheets and unstacked and then reorded based on shared level 0 columns before flattening
    ###################
    # org flattening
    org_final = org_summary.unstack(-1)
    for col in org_final.columns:
        if col[1] in ('count_in', 'num_fraction_in') or col[0].endswith(('_count', '_volume')):
            if col[2] not in col[0]:
                org_final.drop(col,axis=1, inplace=True)
    new_col_order = ['dataset', 'image_name', 'object', 'volume', 'surface_area', 'SA_to_volume_ratio', 
                 'equivalent_diameter', 'extent', 'euler_number', 'solidity', 'axis_major_length', 
                 'ERXLD', 'ERXLD_count', 'ERXLD_volume', 'golgiXER', 'golgiXER_count', 'golgiXER_volume', 
                 'golgiXLD', 'golgiXLD_count', 'golgiXLD_volume', 'golgiXperox', 'golgiXperox_count', 'golgiXperox_volume', 
                 'lysoXER', 'lysoXER_count', 'lysoXER_volume', 'lysoXLD', 'lysoXLD_count', 'lysoXLD_volume', 
                 'lysoXgolgi', 'lysoXgolgi_count', 'lysoXgolgi_volume', 'lysoXmito', 'lysoXmito_count', 'lysoXmito_volume', 
                 'lysoXperox', 'lysoXperox_count', 'lysoXperox_volume', 'mitoXER', 'mitoXER_count', 'mitoXER_volume', 
                 'mitoXLD', 'mitoXLD_count', 'mitoXLD_volume', 'mitoXgolgi', 'mitoXgolgi_count', 'mitoXgolgi_volume', 
                 'mitoXperox', 'mitoXperox_count', 'mitoXperox_volume', 'peroxXER', 'peroxXER_count', 'peroxXER_volume', 
                 'peroxXLD', 'peroxXLD_count', 'peroxXLD_volume']
    new_cols = org_final.columns.reindex(new_col_order, level=0)
    org_final = org_final.reindex(columns=new_cols[0])
    org_final.columns = ["_".join((col_name[-1], col_name[1], col_name[0])) for col_name in org_final.columns.to_flat_index()]

    #renaming, filling "NaN" with 0 when needed, and removing ER_std columns
    for col in org_final.columns:
        if '_count_in_' or '_fraction_in_' in col:
            org_final[col] = org_final[col].fillna(0)
        if col.endswith(("_count_volume","_sum_volume", "_mean_volume", "_median_volume")):
            org_final[col] = org_final[col].fillna(0)
        if col.endswith("_count_volume"):
            org_final.rename(columns={col:col.split("_")[0]+"_count"}, inplace=True)
        if col.startswith("ER_std_"):
            org_final.drop(columns=[col], inplace=True)
    org_final = org_final.reset_index()

    # contacts flattened
    contact_final = contact_summary.unstack(-1)
    contact_final.columns = ["_".join((col_name[-1], col_name[1], col_name[0])) for col_name in contact_final.columns.to_flat_index()]

    #renaming and filling "NaN" with 0 when needed
    for col in contact_final.columns:
        if col.endswith(("_count_volume","_sum_volume", "_mean_volume", "_median_volume")):
            contact_final[col] = contact_final[col].fillna(0)
        if col.endswith("_count_volume"):
            contact_final.rename(columns={col:col.split("_")[0]+"_count"}, inplace=True)
    contact_final = contact_final.reset_index()

    # distributions flattened
    dist_final = dist_summary.unstack(-1)
    dist_final.columns = ["_".join((col_name[1], col_name[0])) for col_name in dist_final.columns.to_flat_index()]
    dist_final = dist_final.reset_index()

    # regions flattened & normalization added
    regions_final = regions_summary.unstack(-1)
    regions_final.columns = ["_".join((col_name[1], col_name[0])) for col_name in regions_final.columns.to_flat_index()]
    regions_final['nuc_area_fraction'] = regions_final['nuc_volume'] / regions_final['cell_volume']
    regions_final = regions_final.reset_index()

    # combining them all
    combined = pd.merge(org_final, contact_final, on=["dataset", "image_name"], how="outer")
    combined = pd.merge(combined, dist_final, on=["dataset", "image_name"], how="outer")
    combined = pd.merge(combined, regions_final, on=["dataset", "image_name"], how="outer").set_index(["dataset", "image_name"])
    combined.columns = [col.replace('sum', 'total') for col in combined.columns]

    ###################
    # export summary sheets
    ###################
    org_summary.to_csv(out_path + f"/{out_preffix}per_org_summarystats.csv")
    contact_summary.to_csv(out_path + f"/{out_preffix}per_contact_summarystats.csv")
    dist_summary.to_csv(out_path + f"/{out_preffix}distribution_summarystats.csv")
    regions_summary.to_csv(out_path + f"/{out_preffix}per_region_summarystats.csv")
    combined.to_csv(out_path + f"/{out_preffix}summarystats_combined.csv")

    print(f"Processing of {fl_count} files from {ds_count} dataset(s) is complete.")
    return f"{fl_count} files from {ds_count} dataset(s) were processed"

In [155]:
_batch_summary_stats(csv_path_list=[Path(os.path.expanduser("~")) / "Documents/Python_Scripts/Infer-subc/quant"], 
                     out_path="C:/Users/Shannon/Documents/Python_Scripts/Infer-subc/quant", 
                     out_preffix='20231110_test_')

C:\Users\Shannon\AppData\Local\Temp\ipykernel_26164\3077410197.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  contact_cnt[["orgA", "orgB"]] = contact_cnt["object"].str.split('X', expand=True)
C:\Users\Shannon\AppData\Local\Temp\ipykernel_26164\3077410197.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  contact_cnt[["orgA", "orgB"]] = contact_cnt["object"].str.split('X', expand=True)
C:\Users\Shannon\AppData\Local\Temp\ipykernel_26164\3077410197.py:62: SettingWithCopyWarning: 
A value is trying to 

Processing of 4 files from 1 dataset(s) is complete.


c:\Users\Shannon\anaconda3\envs\infer-subc\lib\site-packages\pandas\core\internals\blocks.py:2536: RuntimeWarning: invalid value encountered in cast
  values = values.astype(str)
c:\Users\Shannon\anaconda3\envs\infer-subc\lib\site-packages\pandas\core\internals\blocks.py:2536: RuntimeWarning: invalid value encountered in cast
  values = values.astype(str)
c:\Users\Shannon\anaconda3\envs\infer-subc\lib\site-packages\pandas\core\internals\blocks.py:2536: RuntimeWarning: invalid value encountered in cast
  values = values.astype(str)
c:\Users\Shannon\anaconda3\envs\infer-subc\lib\site-packages\pandas\core\internals\blocks.py:2536: RuntimeWarning: invalid value encountered in cast
  values = values.astype(str)


'4 files from 1 dataset(s) were processed'

__________________
# Quality control
1. Do any of the values trend with the size of the cell?

## Andy's original codes

In [ ]:
def summarize_by_id(stats_in:pd.DataFrame,agg_fn: List) -> pd.DataFrame:
    """ 
    """
    summary = stats_in.groupby(['ID']).agg(agg_fn)
    summary.columns = ["_".join(col_name).rstrip('_') for col_name in summary.columns.to_flat_index()]
    return summary

In [ ]:
def create_stats_summary(summary_df:pd.DataFrame) -> pd.DataFrame:
    """
    """
    column_names = summary_df.columns

    def frac(x):
        return (x>0).sum()/x.count() 

    math_cols = ['ID', 'mean_intensity',
        'standard_deviation_intensity',
        'min_intensity','max_intensity', 'equivalent_diameter',
        'euler_number', 'extent']
    vol_cols = ['ID','volume']
    overlap_cols = ['ID'] + [col for col in column_names if col.endswith('_overlap')]
    labels_cols = ['ID'] + [col for col in column_names if col.endswith('_labels')]
   
    agg_func_math = ['sum', 'mean', 'median', 'min', 'max', 'std','count']
    agg_func_overlap = ['sum', 'mean', 'median','count',frac]
    agg_func_labels = ['sum']
    agg_func_vol = ['sum', 'mean', 'median', 'min', 'max', 'std', 'var']

    math_summary = summarize_by_id( summary_df[math_cols] , agg_func_math)
    
    # label_stats = fix_list_col(summary_df[labels_cols])
    label_summary = summarize_by_id( summary_df[labels_cols] , agg_func_labels)
    overlap_summary = summarize_by_id( summary_df[overlap_cols] ,agg_func_overlap)
    vol_summary = summarize_by_id( summary_df[vol_cols] , agg_func_vol)
    result = pd.concat([math_summary, vol_summary, overlap_summary, label_summary], axis=1)

    result.insert(loc=0,column="ID",value=result.index)

    return result

In [ ]:
# for a list of "prefixes"  collect stats + cross stats masked by cytosol (including nuclei masked by cellmask)

def _summarize_organelle_stats(int_path: Union[Path,str], 
                              organelle_names: List[str]):
    """  
    """
    # write out files... 

    if isinstance(int_path, str): int_path = Path(int_path)

    if not Path.exists(out_path):
        Path.mkdir(out_path)
        print(f"making {out_path}")

    all_stats_df = pd.DataFrame()
    all_cross_stats_df = pd.DataFrame()
    all_proj_stats_df = pd.DataFrame()
    
    for target in organelle_names:
        stat_file_list = sorted( int_path.glob(f"*{target}-stats.csv") )

        stats_df = pd.DataFrame()
        cross_stats_df = pd.DataFrame()
        proj_stats_df = pd.DataFrame()

        for stats_f in stat_file_list:
            stem = stats_f.stem.split("-")[0]
            # stats load the csv
            stats = load_stats_csv(out_path,stem, target)
            # projection stats
            proj = load_proj_stats_csv(out_path,stem, target)
            # cross stats
            cross = load_cross_stats_csv(out_path,stem, target)

            stats_df = pd.concat([stats_df,stats],axis=0, join='outer')
            proj_stats_df = pd.concat([proj_stats_df,proj],axis=0, join='outer')
            cross_stats_df = pd.concat([cross_stats_df,cross],axis=0, join='outer')
        

        ## maybe merge into all the possible files?
        # summary_df = pd.DataFrame(index=[f.stem.split("-")[0] for f in stat_file_list])
        # cross_stats_df = pd.DataFrame(index=[f.stem.split("-")[0] for f in stat_file_list])
        # proj_stats_df = pd.DataFrame(index=[f.stem.split("-")[0] for f in stat_file_list])

        summary_df = create_stats_summary(stats_df)
        summary_df.insert(loc=1,column="organelle",value=target)
        cross_summary_df = summarize_cross_stats(cross_stats_df)
        ## cross_summary_df = pivot_cross_stats(cross_stats_df)  #makes a wide version... but has a bug
        cross_summary_df.insert(loc=1,column="organelle",value=target)

        all_stats_df = pd.concat([all_stats_df,summary_df],axis=0)
        all_proj_stats_df = pd.concat([all_proj_stats_df,proj_stats_df],axis=0)
        all_cross_stats_df = pd.concat([all_cross_stats_df,cross_summary_df],axis=0)
    

    return all_stats_df, all_proj_stats_df, all_cross_stats_df
        



In [ ]:
from infer_subc.utils.stats_helpers import summarize_organelle_stats, dump_organelle_summary_tables

# all the imaging data goes here.
data_root_path = Path(os.path.expanduser("~")) / "Projects/Imaging/data"
# linearly unmixed ".czi" files are here
raw_data_path = data_root_path / "raw"
# save output ".tiff" files here could be different than out
int_data_path = data_root_path / "out"
# save stats here
out_data_path = data_root_path / "out"


all_stats_df, all_proj_stats_df, all_cross_stats_df = summarize_organelle_stats( int_path, organelle_names )


In [ ]:
def _dump_organelle_summary_tables(
                    int_path: Union[Path,str], 
                    out_path: Union[Path, str], 
                    organelle_names: List[str]= ["nuclei","golgi","peroxi"] ) -> int:
    """
    get summary and all cross stats between organelles `a` and `b`
    calls `get_summary_stats_3D`
    """

    if not Path.exists(out_path):
        Path.mkdir(out_path)
        print(f"making {out_path}")


    all_stats_df, all_proj_stats_df, all_cross_stats_df = summarize_organelle_stats( int_path, organelle_names )

    csv_path = out_path / f"summary-stats.csv"
    all_stats_df.to_csv(csv_path)

    csv_path = out_path / f"summary-proj-stats.csv"
    all_proj_stats_df.to_csv(csv_path)

    csv_path = out_path / f"summary-cross-stats.csv"
    all_cross_stats_df.to_csv(csv_path)

    return 1



In [ ]:
n_files = dump_organelle_summary_tables(out_data_path, 
                     out_data_path, 
                     organelle_names)

n_files

Make some wrappers to deal with reading our summary stats into pandas properly.


In [ ]:
def load_summary_stats_csv(in_path: Path) -> pd.DataFrame:
    """ helper to load the summary stats csv: summary-stats.csv
    returns pandas DataFrame """
    csv_path = in_path / f"summary-stats.csv"
    summary_df = pd.read_csv(csv_path, index_col=0)
    # need to convert columns *_labels
    list_cols = [col for col in summary_df.columns if "labels" in col] #if col.contains("label")
    summary_df = fix_int_list_cols(summary_df,list_cols)
    return summary_df


def load_summary_proj_stats_csv(in_path: Path) -> pd.DataFrame:
    """ helper to load summary projection stats csv: summary-proj-stats.csv
    returns pandas DataFrame """
    obj_cols =  ['ID', 'organelle','mask','radial_n_bins','n_z']  # leave alone
    str_cols = [ 'radial_bins']
    int_cols = ['radial_cm_vox_cnt', 'radial_org_vox_cnt', 'radial_org_intensity', 'radial_n_pix','zernike_n', 'zernike_m', 'z','z_cm_vox_cnt','z_org_vox_cnt', 'z_org_intensity', 'z_nuc_vox_cnt']
    float_cols = ['radial_cm_cv', 'radial_org_cv', 'radial_img_cv','zernike_cm_mag', 'zernike_cm_phs','zernike_obj_mag', 'zernike_obj_phs', 'zernike_nuc_mag','zernike_nuc_phs', 'zernike_img_mag']

    csv_path = in_path / f"summary-proj-stats.csv"
    proj = pd.read_csv(csv_path, index_col=0)
    proj = fix_str_list_cols(proj, str_cols)
    proj = fix_int_list_cols(proj, int_cols)
    proj = fix_float_list_cols(proj, float_cols)
    return proj
        

def load_summary_cross_stats_csv(in_path: Path) -> pd.DataFrame:
    """ helper to load summary cross- stats csv: summary-cross-stats.csv
    returns pandas DataFrame """

    csv_path = in_path / f"summary-cross-stats.csv"
    summary_df = pd.read_csv(csv_path, index_col=0)

    list_cols = [col for col in summary_df.columns if "label" in col] #if col.contains("label")
    str_list_cols = [col for col in list_cols if "__" in col]
    int_list_cols = [col for col in list_cols if "__" not in col]

    summary_df = fix_str_list_cols(summary_df,str_list_cols)
    summary_df = fix_int_list_cols(summary_df,int_list_cols)

    return summary_df
    


In [ ]:

#summary_shell.head()
test = load_summary_stats_csv(out_data_path)
test_proj = load_summary_proj_stats_csv(out_data_path)
test_cross = load_summary_cross_stats_csv(out_data_path)